In [ ]:
import os
import fitz  # PyMuPDF
import re
import pandas as pd
import pandas as pd
import spacy
 
# Load SpaCy model
nlp = spacy.load("en_core_web_sm")
# Define an empty DataFrame with the desired column names
initial_columns  = ["File Name", "RECEIVED ON", "REGISTERED ON", "DECIDED ON", "DURATION", "Case Number", "CNR Number",
           "Court Title", "Judge Name", "Claim Under Section", "Brief Description of the Accident", 
           "Date of Accident", "Place of Accident", "Death/Injury Details", "Registration No of vehicle 1", 
           "Deceased/Victim Name", "Deceased/Victim Age", "Deceased/Victim Income", "Deceased/Victim's Occupation",
           "Account Number", "Bank Name", "IFSC Code", "Claim Rs.", "Advocate for Applicants",
           "Advocate for opponent No.1", "Advocate for opponent No.2", "Name of Steno", "Order uploaded on", 
           "Date of Order","Insurance company name","Medical expenses","Police station name","First hospital name",
           "Second hospital name","Interest Rate"]
 
# Assuming the maximum number of individual and organization opponents
max_opponents_individual = 5
max_opponents_organization = 5
 
# Define opponent individual columns
opponent_individual_columns = []
for i in range(1, max_opponents_individual + 1):
    opponent_individual_columns.extend([
        f"Opponent {i} Number", f"Opponent {i} Name", f"Opponent {i} Age",
        f"Opponent {i} Occupation", f"Opponent {i} Address"
    ])
 
# Define opponent organization columns
opponent_organization_columns = []
for i in range(1, max_opponents_organization + 1):
    opponent_organization_columns.extend([
        f"Opponent Org {i} Number", f"Opponent Org {i} Name", f"Opponent Org {i} Address"
    ])
 
# Combine all columns
all_columns = initial_columns + opponent_individual_columns
df = pd.DataFrame(columns=all_columns)
 
def extract_and_clean_text_from_pdf(pdf_path):
    # Open the PDF file
    doc = fitz.open(pdf_path)
    text = ""
    for page in doc:
        text += page.get_text()
    doc.close()
 
    # Clean the extracted text
    cleaned_text = re.sub(r'\s+', ' ', text)  # Remove unwanted spaces
    cleaned_text = cleaned_text.strip()  # Remove leading and trailing spaces
   
    return cleaned_text
 
def extract_applicants(cleaned_text, first_two_pages_text):
    # Updated regular expression patterns
    detailed_pattern= re.compile(
    r'(\d+)-\s*(Mrs\.|Mr\.|Smt\.|Miss)?\s*([\w\s.]+?)\s+Age\s+(\d+)\s+years,\s+Occ\s*:\s*([^\n,]+)(?:,\s+)?(?:Both\s+R\/?at\s+|R\/?o\s+)?([\w\s,.-]*?)\s*\.*\s*(?:\.\.\.)?\s*Applicants?.*?(?=Versus|v\/s|V\/s|v \/ s|V \/ s|versus)',re.IGNORECASE | re.DOTALL)
 
    simple_pattern = re.compile(
    r'(\d+)-\s*(?:Shri\.\s*)?((?:(?!M\.A\.C\.P\. No\.)[^\d,\n])+).*?Age.*?(\d+).*?Occ\s*:\s*([^\n]+)',re.IGNORECASE | re.DOTALL)


    # Extract addresses
    address_pattern = re.compile(
        r'R[/@]t?\s*[-–]?\s*([\w\s,.()]+)(?=\.\s*|,)',
        re.IGNORECASE
    )
    addresses = address_pattern.findall(first_two_pages_text)

    detailed_applicants = detailed_pattern.findall(cleaned_text)
    simple_applicants = simple_pattern.findall(first_two_pages_text)

    applicants = detailed_applicants[:6] + simple_applicants[:6 - len(detailed_applicants)]

    applicant_data = {}
    for i, details in enumerate(applicants, start=1):
        if len(details) == 6:
            # Unpack 6 values
            num, prefix, name, age, occupation, _ = details
            applicant_data[f'Applicant {i} Number'] = num.strip() if num else " "
            applicant_data[f'Applicant {i} Name'] = f"{prefix.strip()} {name.strip()}" if prefix else name.strip()
            applicant_data[f'Applicant {i} Age'] = age.strip()
            applicant_data[f'Applicant {i} Occupation'] = occupation.strip()
        elif len(details) == 4:
            # Unpack 4 values
            num, name, age, occupation = details
            applicant_data[f'Applicant {i} Number'] = num.strip() if num else " "
            applicant_data[f'Applicant {i} Name'] = name.strip()
            applicant_data[f'Applicant {i} Age'] = age.strip()
            applicant_data[f'Applicant {i} Occupation'] = occupation.strip()
        # Assign address to each applicant
        if i - 1 < len(addresses):
            applicant_data[f'Applicant {i} Address'] = addresses[i - 1].strip()
        else:
            applicant_data[f'Applicant {i} Address'] = ""

    return applicant_data

 
def add_applicant_columns(df, max_applicants):
    for i in range(1, max_applicants + 1):
        df[f'Applicant {i} Number'] = None
        df[f'Applicant {i} Name'] = None
        df[f'Applicant {i} Age'] = None
        df[f'Applicant {i} Occupation'] = None

def extract_opponents(cleaned_text, first_two_pages_text):
    # Existing detailed opponent pattern
    detailed_opponent_pattern = re.compile(
        r'(\d+)-?\s*(?:(Mr\.|Ms\.|Mrs\.|Smt\.|The Manager,|M/s)\s+)?([A-Za-z\s.]+?),?\s*Age\s*[:-]?\s*(\d+)\s*years?,?\s*Occ\.*\s*[:-]?\s*([A-Za-z\s]+),?\s*R?/?at\s*([A-Za-z0-9,\s.\/-]+)',
        re.IGNORECASE
    )

    general_opponent_pattern = re.compile(
        r'(?:Vs\.|V/s|Versus)\s+([A-Za-z\s.]+?)(?:\s+&\s+|\s+and\s+|\s*[/]\s*|\s*[\]\[]\s*|$)',
        re.IGNORECASE
    )

    # Ignore pattern for specific lines
    ignore_pattern = re.compile(r'CNR No\.\s*\n\d+\s*\n[A-Z0-9-]+\s*\nM\.A\.C\.P\. No\.\d{1,}/\d{4}\s*\nJudgment', re.IGNORECASE)

    # Apply ignore pattern to the complete text
    cleaned_text = re.sub(ignore_pattern, '', cleaned_text)

    # Extract detailed opponents from the cleaned text
    detailed_opponents = detailed_opponent_pattern.findall(cleaned_text)

    # Extract general opponents from only the first two pages
    general_opponents = general_opponent_pattern.findall(first_two_pages_text)

    opponent_data = {}

    # Process detailed opponents
    for i, (num, prefix, name, age, occupation, address) in enumerate(detailed_opponents, start=1):
        opponent_data[f'Opponent {i} Number'] = num.strip()
        opponent_data[f'Opponent {i} Name'] = f"{prefix.strip()} {name.strip()}" if prefix else name.strip()
        opponent_data[f'Opponent {i} Age'] = age.strip()
        opponent_data[f'Opponent {i} Occupation'] = occupation.strip()
        opponent_data[f'Opponent {i} Address'] = address.strip()

    # Process general opponents (only from the first two pages)
    for i, opponent in enumerate(general_opponents, start=len(detailed_opponents) + 1):
        opponent = opponent.strip().rstrip(',').strip()
        opponent_data[f'Opponent {i} Name'] = opponent

    return opponent_data

 
def process_pdfs_in_folder(folder_path, df):
    all_files = os.listdir(folder_path)
    pdf_files = [file for file in all_files if file.lower().endswith('.pdf')]
    for pdf_file in pdf_files:
        pdf_path = os.path.join(folder_path, pdf_file)
        print(f"Processing {pdf_file}...")
        cleaned_text = extract_and_clean_text_from_pdf(pdf_path)
        doc = nlp(cleaned_text)
        
        
        doc = fitz.open(pdf_path)
        first_two_pages_text = ""
        for page_num in range(min(2, doc.page_count)):
            first_two_pages_text += doc[page_num].get_text()
 
        # Define patterns for each date
        received_or_presented_on_pattern = re.compile(r'(?:RECEIVED ON|Presented on)\s*:\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        registered_on_pattern = re.compile(r'Registered on\s*:\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        decided_on_pattern = re.compile(r'Decided on\s*:\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        duration_pattern_multiline = re.compile(r'Duration\s*:\s*Ys/\s*Ms/\s*Ds/\s*\n\s*(\d{2})\s+(\d{2})\s+(\d{2})', re.IGNORECASE)
        duration_pattern_singleline = re.compile(r'DURATION\s*:\s*(\d+)(?:Ys|Y)[.\s]*(\d+)(?:Ms|M)[.\s]*(\d+)(?:Ds|D)[.\s]*', re.IGNORECASE)
 
        # Search for each date
        received_on_match = received_or_presented_on_pattern.search(cleaned_text)
        registered_on_match = registered_on_pattern.search(cleaned_text)
        decided_on_match = decided_on_pattern.search(cleaned_text)
 
        # Extract dates
        received_on = received_on_match.group(1) if received_on_match else " "
        registered_on = registered_on_match.group(1) if registered_on_match else " "
        decided_on = decided_on_match.group(1) if decided_on_match else " "
 
        # Extract durations
        duration_match_multiline = duration_pattern_multiline.search(cleaned_text)
        duration_match_singleline = duration_pattern_singleline.search(cleaned_text)
        if duration_match_multiline:
            years, months, days = duration_match_multiline.groups()
            duration = f"{years} years, {months} months, {days} days"
        elif duration_match_singleline:
            years, months, days = duration_match_singleline.groups()
            duration = f"{years} years, {months} months, {days} days"
        else:
            duration = " "
 
        # Case Number
        case_number_pattern = re.compile(
            r'M\.?A\.?C\.?P\.?\s*No\.?\s*(\d+)(?:\/(\d+))?',
            re.IGNORECASE
        )
        case_number_match = case_number_pattern.search(cleaned_text)
        if case_number_match:
            # Construct the case number from the matched groups
            case_number = "MACP No." + case_number_match.group(1)
            if case_number_match.group(2):
                case_number += "/" + case_number_match.group(2)
        else:
            case_number = ""

 
        # CNR Number
        cnr_number_pattern = re.compile(
            r'(?:CNR No\.?|CNR)\s*:? MHPU\d{2}-?\s*0?\d{3,6}-\d{4}|MHPU\d{2}-?\s*0?\d{3,6}-\d{4}|MHPU\d{2}-?\d{3,6}-\d{4}',
            re.IGNORECASE
        )
        cnr_number_match = cnr_number_pattern.search(cleaned_text)
        if cnr_number_match:
            cnr_number = cnr_number_match.group(0).replace("CNR No. ", "").replace("CNR No", "").replace("CNR ", "").replace("\n", "").replace(" ", "")
        else:
            cnr_number = ""

 
        court_title_pattern = re.compile(
            r'BEFORE THE (NATIONAL LOK-ADALAT, HELD AT PUNE|MEMBER, MOTOR ACCIDENT CLAIMS\s+TRIBUNAL, PUNE AT PUNE)',
            re.IGNORECASE | re.DOTALL
        )
        court_title_match = court_title_pattern.search(cleaned_text)
        if court_title_match:
            court_title = court_title_match.group(0).strip()
        else:
            court_title = ""


 
        # Judge Name
        judge_name_pattern = re.compile(r'Digitally signed by (.+?) Date:')
        judge_name_match = judge_name_pattern.search(cleaned_text)
        judge_name = judge_name_match.group(1).strip() if judge_name_match else ""
 
        old_claim_pattern = re.compile(r'Claim Application under Section\s+(\d+)\s+of the Motor Vehicles Act')
        old_claim_match = old_claim_pattern.search(cleaned_text)

        # New Claim Under Section pattern (for Legal Services Authority Act, 1987)
        new_claim_pattern = re.compile(r'Pune under Section (\d+) of the Legal Services Authority Act, 1987')
        new_claim_match = new_claim_pattern.search(cleaned_text)

        # Determine which pattern matches and use that
        if old_claim_match:
            claim_info = f"Section {old_claim_match.group(1)} of the Motor Vehicles Act"
        elif new_claim_match:
            claim_info = f"Section {new_claim_match.group(1)} of the Legal Services Authority Act, 1987"
        else:
            claim_info = ""
 
        accident_description_pattern = re.compile(r'The petition in short, is as under : (.*?)(?: On|$)', re.DOTALL)
        accident_description_match = accident_description_pattern.search(cleaned_text)
        accident_description = accident_description_match.group(1).strip() if accident_description_match else ""
 
        # Date of Accident
        date_pattern = re.compile(r'(\d{2}\.\d{2}\.\d{4})')
        date_match = date_pattern.search(cleaned_text)
        accident_date = date_match.group(1).strip() if date_match else ""

        # Place of Accident
        place_pattern = re.compile(r'on\s([^\,\.]+? road,? [^\,\.]+)|in front of ([^\,\.]+), near [^\,\.]+, ([^\,\.]+)', re.IGNORECASE)
        place_match = place_pattern.search(cleaned_text)
        if place_match:
            if place_match.group(1):
                accident_place = place_match.group(1).strip()
            else:
                accident_place = place_match.group(2).strip() + ", " + place_match.group(3).strip()
        else:
            accident_place = ""

 
        # Death/Injury Details
        death_injury_pattern = re.compile(r'(deceased was seriously injured and succumbed to injuries|account of accidental death of [\w\s]+)', re.IGNORECASE)
        death_injury_match = death_injury_pattern.search(cleaned_text)
        death_injury_details = death_injury_match.group(0) if death_injury_match else ""
 
        # Registration No of vehicle 1
        #registration_pattern = re.compile(r'registration No\.\s*([A-Z0-9-]+)')
        registration_pattern = re.compile(r'registration No\.?\s*([A-Z]{2}-?\s?[0-9]{2}-?\s?[A-Z]*-?\s?[0-9]{4})',re.IGNORECASE)
        registration_match = registration_pattern.search(cleaned_text)
        registration_number = registration_match.group(1).strip() if registration_match else ""
 
        # Deceased/Victim Name
        #name_pattern = re.compile(r'Deceased\s+([A-Za-z]+\s+[A-Za-z]+\s+[A-Za-z]+)')
#         name_pattern = re.compile(r'Deceased\s+([A-Za-z]+(?:\s+[A-Za-z]+){1,2})')
#         name_match = name_pattern.search(cleaned_text)
#         deceased_victim_name = name_match.group(1).strip() if name_match else ""
       
        name_pattern = re.compile(r'Deceased\s+([A-Za-z]+(?:\s+[A-Za-z]+){0,2})', re.IGNORECASE)
        deceased_names = name_pattern.findall(cleaned_text)
        if deceased_names:
            cleaned_deceased_name = deceased_names[0].strip()
        else:
            cleaned_deceased_name = ""
 
        # Deceased/Victim Age
        age_pattern = re.compile(r'age(?:d)?\s+(\d+)(?:\s+years(?:\s+old)?)?', re.IGNORECASE)
        age_match = age_pattern.search(cleaned_text)
        deceased_victim_age = age_match.group(1) if age_match else ""
 
        # Deceased/Victim Income
        income_pattern = re.compile(r'(?:earning|salary)\s+Rs\.\s*([0-9,/-]+)(?:\s+per month|\s+monthly)?', re.IGNORECASE)
        income_match = income_pattern.search(cleaned_text)
        deceased_victim_income = income_match.group(1) if income_match else ""
 
        # Deceased/Victim's Occupation
        occupation_pattern = re.compile(r'worked in ([\w\s]+) as ([\w\s]+)')
        occupation_match = occupation_pattern.search(cleaned_text)
        if occupation_match:
            company = occupation_match.group(1).strip()
            position = occupation_match.group(2).strip()
            deceased_victim_occupation = f"{position} at {company}"
        else:
            deceased_victim_occupation = ""
 
        # Account Number
        account_number_pattern = re.compile(r'Account Number\s+(\d+)', re.IGNORECASE)
        account_number_match = account_number_pattern.search(cleaned_text)
        account_number = account_number_match.group(1).strip() if account_number_match else ""
        
        account_name_pattern = re.compile(r'Account Name\s*[-:]\s*([-\w\s,]+)',re.IGNORECASE)
        account_name_match = account_name_pattern.search(cleaned_text)
        account_name = account_name_match.group(1).strip() if account_name_match else ""
 
        # Bank Name
        #bank_name_pattern = re.compile(r'Name of Bank\s*(.*?)(?:\.|, IFSC Code)', re.IGNORECASE | re.DOTALL)
        bank_name_pattern = re.compile(r'(State Bank of India),\s*(\w+)\s+Court Branch,\s*(Pune)', re.IGNORECASE)
        bank_name_match = bank_name_pattern.search(cleaned_text)
        bank_name = bank_name_match.group(1).strip() if bank_name_match else ""
 
        # IFSC Code
        #ifsc_code_pattern = re.compile(r'IFSC Code\s*(\S+)', re.IGNORECASE)
        ifsc_code_pattern = re.compile(r'IFSC Code\s*[-:]*\s*(SBIN\d{6})',re.IGNORECASE)
        ifsc_code_match = ifsc_code_pattern.search(cleaned_text)
        ifsc_code = ifsc_code_match.group(1).strip() if ifsc_code_match else ""
 
        # Claim Rs.
        claim_pattern = re.compile(r'Claim Rs\.\s*([\d,/-]+)')
        claim_match = claim_pattern.search(cleaned_text)
        claim_amount = claim_match.group(1).strip() if claim_match else ""
 
        # Advocate for Applicants
        advocate_pattern = re.compile(r'Advocate for Applicants\s*:\s*([\w\s.]+?)(?=,\s*Shri\.|For opponent|$)',re.IGNORECASE | re.DOTALL)
        advocate_match = advocate_pattern.search(cleaned_text)
        advocate_name = advocate_match.group(1).strip() if advocate_match else ""
 
        # Advocate for opponent No.1
        advocate_opponent1_pattern = re.compile(r'Advocate for opponent No\.1\s*:\s*(.*?)(?=\s*Advocate for opponent No\. 2)', re.IGNORECASE | re.DOTALL)
        advocate_opponent1_match = advocate_opponent1_pattern.search(cleaned_text)
        advocate_opponent1_name = advocate_opponent1_match.group(1).strip() if advocate_opponent1_match else ""
 
        # Advocate for opponent No.2
        #advocate_opponent2_pattern = re.compile(r'Advocate for opponent No\. 2\s*:\s*(.*?)(?=\s*Claim Application|\n|$)', re.IGNORECASE | re.DOTALL)
        advocate_opponent2_pattern = re.compile(r'Advocate for opponent No\. 2\s*:\s*((?:Shri\.?\s+[A-Z]\.\s+[A-Z]\.\s+\w+)(?:\s*,\s*(?:Shri\.?\s+[A-Z]\.\s+[A-Z]\.\s+\w+))*)', re.IGNORECASE | re.DOTALL)
        advocate_opponent2_match = advocate_opponent2_pattern.search(cleaned_text)
        advocate_opponent2_name = advocate_opponent2_match.group(1).strip() if advocate_opponent2_match else ""
 
        # Name of Steno
        steno_pattern = re.compile(r'Name of Steno : (.+?) Date of order')
        steno_match = steno_pattern.search(cleaned_text)
        steno_name = steno_match.group(1).strip() if steno_match else ""
 
        # Order uploaded on
        order_uploaded_pattern = re.compile(r'Order uploaded on : (\d{2}\.\d{2}\.\d{4})')
        order_uploaded_match = order_uploaded_pattern.search(cleaned_text)
        order_uploaded_date = order_uploaded_match.group(1).strip() if order_uploaded_match else ""
 
        # Date of Order
        date_of_order_pattern = re.compile(r'Date of order : (\d{2}\.\d{2}\.\d{4})')
        date_of_order_match = date_of_order_pattern.search(cleaned_text)
        date_of_order = date_of_order_match.group(1).strip() if date_of_order_match else ""
        insurance_company_pattern = re.compile(r'\b(?:[A-Za-z]+\s)*(?:Insurance|Insurer|Ltd\.|Limited|Corporation|Corp\.|Company|Co\.|Group)\b',re.IGNORECASE)
        insurance_company_match = insurance_company_pattern.search(cleaned_text)
        insurance_company_name = insurance_company_match.group(0).strip() if insurance_company_match else " "
        medical_expenses_pattern = re.compile(r'Medical expenses Rs\.\s*([\d,/-]+)',re.IGNORECASE)
        medical_expenses_match = medical_expenses_pattern.search(cleaned_text)
        medical_expenses = medical_expenses_match.group(1).strip() if medical_expenses_match else " "
        fir_number_pattern = re.compile(r'FIR Exh\.\s*(\d+)',re.IGNORECASE)
        fir_number_match = fir_number_pattern.search(cleaned_text)
        fir_number = fir_number_match.group(1).strip() if fir_number_match else " "
        police_station_pattern = re.compile(r'Police Station,\s*([A-Za-z ]+)',re.IGNORECASE)
        police_station_match = police_station_pattern.search(cleaned_text)
        police_station_name = police_station_match.group(1).strip() if police_station_match else " "

        hospital_pattern = re.compile(r'(?:First hospital details\s+)?([A-Za-z ]+ Hospital)\s*(?:,|\b)(?:\s*Second hospital details\s+([A-Za-z ]+ Hospital))?',re.IGNORECASE)
        hospital_match = hospital_pattern.search(cleaned_text)
        first_hospital = hospital_match.group(1).strip() if hospital_match and hospital_match.group(1) else " "
        second_hospital = hospital_match.group(2).strip() if hospital_match and hospital_match.group(2) else None
        applicant_data = extract_applicants(cleaned_text, first_two_pages_text)
        opponent_data = extract_opponents(cleaned_text, first_two_pages_text)

        
        written_statement_pattern = re.compile(r'(Exh\.\s*\d+\s+(?:opponent\s*No\.?1|respondent)\s+filed\s+written\s+statement)(.*?)(?=Exh\.|\Z)',re.IGNORECASE)
        written_statement_match = written_statement_pattern.findall(cleaned_text)
        written_statement_content = " ".join([match[1].strip() for match in written_statement_match])

        written_statement_opponent2_pattern = re.compile(r'(Exh\.\s*\d+\s+opponent\s*No\.?2\s+filed\s+written\s+statement)(.*?)(?=Exh\.|\Z)',re.IGNORECASE | re.DOTALL)
        written_statement_opponent2_matches = written_statement_opponent2_pattern.findall(cleaned_text)
        written_statement_opponent2_content = " ".join([match[1].strip() for match in written_statement_opponent2_matches])
        
        # Merged pattern for judgment date
        judgment_date_pattern = re.compile(
            r'Delivered on(?: this)? (\d{1,2}(?:st|nd|rd|th)?(?: day of)? [^\d\W_]+(?:,)? \d{4})|'
            r'Delivered on (?:this )?(\d{1,2})(?:st|nd|rd|th)?\s+Day of (\w+)\s+(\d{4})',
            re.IGNORECASE
        )

        # Search for the pattern in the cleaned text
        judgment_date_match = judgment_date_pattern.search(cleaned_text)

        # Extract the judgment date if a match is found
        if judgment_date_match:
            if judgment_date_match.group(1):
                judgment_date = judgment_date_match.group(1)
            else:
                day = judgment_date_match.group(2)
                month = judgment_date_match.group(3)
                year = judgment_date_match.group(4)
                judgment_date = f"{day} {month} {year}"
        else:
            judgment_date = " "
            
        loss_of_consortium_pattern = re.compile(r'Loss of Consortium\s*Rs\.([\d,/-]+)', re.IGNORECASE)

        # Search for the pattern in the text
        loss_of_consortium_match = loss_of_consortium_pattern.search(cleaned_text)

        # Extract the Loss of Consortium amount if a match is found
        loss_of_consortium_amount = loss_of_consortium_match.group(1).strip() if loss_of_consortium_match else " "
        
        
        loss_of_estate_pattern = re.compile(r'Loss of Estate\s*Rs\.([\d,/-]+)', re.IGNORECASE)

        # Search for the pattern in the text
        loss_of_estate_match = loss_of_estate_pattern.search(cleaned_text)

        # Extract the Loss of Estate amount if a match is found
        loss_of_estate_amount = loss_of_estate_match.group(1).strip() if loss_of_estate_match else " "
            
            
        marital_status_pattern = re.compile(r'Deceased\s+(?:was\s+)?(married|bachelor)', re.IGNORECASE)
        marital_status_match = marital_status_pattern.search(cleaned_text)
        if marital_status_match:
            marital_status = marital_status_match.group(1)
        else:
            marital_status = " "
              
        witness_no_1_pattern = re.compile(r'([A-Za-z\s.]+)\s+is\s+examined\s+as\s+witness\s+No\.?\s*1', re.IGNORECASE)

        # Search for witness No. 1 in the text
        witness_no_1_match = witness_no_1_pattern.search(cleaned_text)

        # Extract the witness number
        witness_no_1 = witness_no_1_match.group() if witness_no_1_match else ""   
        
        witness_no_2_pattern = re.compile(r'([A-Za-z\s.]+)\s+as\s+witness\s+No\.?\s*2', re.IGNORECASE)

        # Search for witness No. 2 in the text
        witness_no_2_match = witness_no_2_pattern.search(cleaned_text)

        # Extract the witness number
        witness_no_2 = witness_no_2_match.group() if witness_no_2_match else ""

        
        
        # Interest Rate
        interest_rate = ""
        phrases_to_check = ['interest on the total compensation', 'interest', 'amount at the rate of']
        for phrase in phrases_to_check:
            if phrase in cleaned_text:
                received_on_index = cleaned_text.find(phrase)
                if received_on_index != -1:
                    received_on_content = cleaned_text[received_on_index + len(phrase):].strip()
                    interest_rate_match = re.search(r'@ (\d+(\.\d+)?)% per annum', received_on_content)
                    if interest_rate_match:
                        interest_rate = interest_rate_match.group(1)
                        break  # Break the loop once interest rate is found

 
        # Create a dictionary to hold the extracted information
        info_dict = {col: "" for col in all_columns} 
        info_dict = {
            "File Name": pdf_file,
            "RECEIVED ON": received_on,
            "REGISTERED ON": registered_on,
            "DECIDED ON": decided_on,
            "DURATION": duration,
            "Case Number": case_number,
            "CNR Number": cnr_number,
            "Court Title": court_title,
            "Judge Name": judge_name,
            "Claim Under Section": claim_info,
            "Brief Description of the Accident": accident_description,
            "Date of Accident": accident_date,
            "Place of Accident": accident_place,
            "Death/Injury Details": death_injury_details,
            "Registration No of vehicle 1": registration_number,
            "Deceased/Victim Name": cleaned_deceased_name,
            "Deceased/Victim Age": deceased_victim_age,
            "Deceased/Victim Income": deceased_victim_income,
            "Deceased/Victim's Occupation": deceased_victim_occupation,
            "Account Number": account_number,
            "Account_Name" : account_name,
            "Bank Name": bank_name,
            "IFSC Code": ifsc_code,
            "Claim Rs.": claim_amount,
            "Advocate for Applicants": advocate_name,
            "Advocate for opponent No.1": advocate_opponent1_name,
            "Advocate for opponent No.2": advocate_opponent2_name,
            "Name of Steno": steno_name,
            "Order uploaded on": order_uploaded_date,
            "Date of Order": date_of_order,
            "Insurance company name":insurance_company_name,
            "Medical expenses":medical_expenses,
            "Fir number":fir_number,
            "Police station name":police_station_name,
            "First hospital name":first_hospital,
            "Second hospital name":second_hospital,
            "Written Statement by Opponent No.1":written_statement_content,
            "Written Statement by Opponent No.2":written_statement_opponent2_content,
            "Judgment Date" : judgment_date,
            "Deceased Marital Status" : marital_status,
            "Witness No 1 " : witness_no_1,
            "Witness No 2 "  : witness_no_2,
            "Loss of Consortium": loss_of_consortium_amount,
            "Loss of Estate Amount": loss_of_estate_amount,
            "Interest Rate": interest_rate
        }
        info_dict.update(applicant_data)
        info_dict.update(opponent_data)  
        # Append the information to a list of DataFrames
        dfs = [df, pd.DataFrame([info_dict])]
        df = pd.concat(dfs, ignore_index=True)
 
    return df
 
# Example usage
folder_path = r"D:\Bajaj\Test"  # Replace with your folder path
df = pd.DataFrame(columns=all_columns)
result_df = process_pdfs_in_folder(folder_path, df)
 
# Save the DataFrame to a CSV file
result_df.to_excel("all Pdf.xlsx", index=False)

In [2]:
import os
import fitz  # PyMuPDF
import re
import pandas as pd
import spacy

# Load SpaCy model
nlp = spacy.load("en_core_web_sm")
import os
from datetime import datetime

# Define an empty DataFrame with the desired column names
initial_columns  = ["File Name", "RECEIVED ON", "REGISTERED ON", "DECIDED ON", "DURATION", "Case Number", "CNR Number",
            "Court Title", "Judge Name", "Claim Under Section", "Brief Description of the Accident",
           "Date of Accident", "Place of Accident", "Death/Injury Details", "Registration No of vehicle 1",
           "Deceased/Victim Name", "Deceased/Victim Age", "Deceased/Victim Income", "Deceased/Victim's Occupation",
           "Account Number", "Bank Name", "IFSC Code", "Claim Rs.", "Advocate for Applicants",
           "Advocate for opponent No.1", "Advocate for opponent No.2", "Name of Steno", "Order uploaded on",
           "Date of Order","Insurance company name","Medical expenses","Police station name","First hospital name",
           "Second hospital name","Interest Rate"]

# Assuming the maximum number of individual and organization opponents

max_opponents_individual = 5
max_opponents_organization = 5

# Define opponent individual columns

opponent_individual_columns = []
for i in range(1, max_opponents_individual + 1):
    opponent_individual_columns.extend([
        f"Opponent {i} Number", f"Opponent {i} Name", f"Opponent {i} Age",
        f"Opponent {i} Occupation", f"Opponent {i} Address"])

# Define opponent organization columns
opponent_organization_columns = []
for i in range(1, max_opponents_organization + 1):
    opponent_organization_columns.extend([
        f"Opponent Org {i} Number", f"Opponent Org {i} Name", f"Opponent Org {i} Address"])

# Combine all columns
all_columns = initial_columns + opponent_individual_columns
df = pd.DataFrame(columns=all_columns)
def extract_and_clean_text_from_pdf(pdf_path):
    # Open the PDF file
    doc = fitz.open(pdf_path)
    text = ""
    for page in doc:
        text += page.get_text()
    doc.close()

    # Clean the extracted text
    cleaned_text = re.sub(r'\s+', ' ', text)  # Remove unwanted spaces
    cleaned_text = cleaned_text.strip()  # Remove leading and trailing spaces
    print(cleaned_text)
    return cleaned_text

def extract_applicants(cleaned_text, first_two_pages_text):
    # Updated regular expression patterns
    detailed_pattern= re.compile(r'(\d+)-\s*(Mrs\.|Mr\.|Smt\.|Miss)?\s*([\w\s.]+?)\s+Age\s+(\d+)\s+years,\s+Occ\s*:\s*([^\n,]+)(?:,\s+)?(?:Both\s+R\/?at\s+|R\/?o\s+)?([\w\s,.-]*?)\s*\.*\s*(?:\.\.\.)?\s*Applicants?.*?(?=Versus|v\/s|V\/s|v \/ s|V \/ s|versus)',re.IGNORECASE | re.DOTALL)
    simple_pattern = re.compile( r'(\d+)-\s*(?:Shri\.\s*)?((?:(?!M\.A\.C\.P\. No\.)[^\d,\n])+).*?Age.*?(\d+).*?Occ\s*:\s*([^\n]+)',re.IGNORECASE | re.DOTALL)
    address_pattern = re.compile(r'R[/@]t?\s*[-–]?\s*([\w\s,.()]+)(?=\.\s*|,)',re.IGNORECASE)

    addresses = address_pattern.findall(first_two_pages_text)
    detailed_applicants = detailed_pattern.findall(cleaned_text)
    simple_applicants = simple_pattern.findall(first_two_pages_text)
    applicants = detailed_applicants[:6] + simple_applicants[:6 - len(detailed_applicants)]
    applicant_data = {}
    for i, details in enumerate(applicants, start=1):
        if len(details) == 6:
            # Unpack 6 values
            num, prefix, name, age, occupation, _ = details
            applicant_data[f'Applicant {i} Number'] = num.strip() if num else " "
            applicant_data[f'Applicant {i} Name'] = f"{prefix.strip()} {name.strip()}" if prefix else name.strip()
            applicant_data[f'Applicant {i} Age'] = age.strip()
            applicant_data[f'Applicant {i} Occupation'] = occupation.strip()

        elif len(details) == 4:
            # Unpack 4 values
            num, name, age, occupation = details
            applicant_data[f'Applicant {i} Number'] = num.strip() if num else " "
            applicant_data[f'Applicant {i} Name'] = name.strip()
            applicant_data[f'Applicant {i} Age'] = age.strip()
            applicant_data[f'Applicant {i} Occupation'] = occupation.strip()

        # Assign address to each applicant
        if i - 1 < len(addresses):
            applicant_data[f'Applicant {i} Address'] = addresses[i - 1].strip()
        else:
            applicant_data[f'Applicant {i} Address'] = ""

    print(applicant_data)
    return applicant_data


def add_applicant_columns(df, max_applicants):
    for i in range(1, max_applicants + 1):
        df[f'Applicant {i} Number'] = None
        df[f'Applicant {i} Name'] = None
        df[f'Applicant {i} Age'] = None
        df[f'Applicant {i} Occupation'] = None

def extract_opponents(cleaned_text, first_two_pages_text):
    # Existing detailed opponent pattern
    detailed_opponent_pattern = re.compile(r'(\d+)-?\s*(?:(Mr\.|Ms\.|Mrs\.|Smt\.|The Manager,|M/s)\s+)?([A-Za-z\s.]+?),?\s*Age\s*[:-]?\s*(\d+)\s*years?,?\s*Occ\.*\s*[:-]?\s*([A-Za-z\s]+),?\s*R?/?at\s*([A-Za-z0-9,\s.\/-]+)',re.IGNORECASE)
    # Updated general opponent pattern to match the provided samples
    general_opponent_pattern = re.compile(r'(?:Vs\.|V/s)\s+([A-Za-z\s.]+?)(?:\s+&\s+|\s+and\s+|\s*[/]\s*|\s*[\]\[]\s*|$)',re.IGNORECASE   )

    # Extract detailed opponents from the complete text
    detailed_opponents = detailed_opponent_pattern.findall(cleaned_text)
    # Extract general opponents from only the first two pages
    general_opponents = general_opponent_pattern.findall(first_two_pages_text)
    opponent_data = {}
    # Process detailed opponents
    for i, (num, prefix, name, age, occupation, address) in enumerate(detailed_opponents, start=1):
        opponent_data[f'Opponent {i} Number'] = num.strip()
        opponent_data[f'Opponent {i} Name'] = f"{prefix.strip()} {name.strip()}" if prefix else name.strip()
        opponent_data[f'Opponent {i} Age'] = age.strip()
        opponent_data[f'Opponent {i} Occupation'] = occupation.strip()
        opponent_data[f'Opponent {i} Address'] = address.strip()

    # Process general opponents (only from the first two pages)
    for i, opponent in enumerate(general_opponents, start=len(detailed_opponents) + 1):
        opponent = opponent.strip().rstrip(',').strip()
        opponent_data[f'Opponent {i} Name'] = opponent
    return opponent_data


def process_pdfs_in_folder(folder_path, df):
    all_files = os.listdir(folder_path)
    pdf_files = [file for file in all_files if file.lower().endswith('.pdf')]
    for pdf_file in pdf_files:
        pdf_path = os.path.join(folder_path, pdf_file)
        print(f"Processing {pdf_file}...")
        cleaned_text = extract_and_clean_text_from_pdf(pdf_path)
        doc = nlp(cleaned_text)
        doc = fitz.open(pdf_path)
        first_two_pages_text = ""
        for page_num in range(min(2, doc.page_count)):
            first_two_pages_text += doc[page_num].get_text()

        # Define patterns for each date

        received_or_presented_on_pattern = re.compile(r'(?:RECEIVED ON|Presented on)\s*:\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        #received_or_presented_on_pattern = re.compile(r'(?:RECEIVED ON|Received on|Presented on)\s*:\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        received_or_presented_on_pattern1 = re.compile(r'Received\s*on\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        registered_on_pattern = re.compile(r'Registered on\s*:\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        decided_on_pattern = re.compile(r'Decided on\s*:\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        duration_pattern_multiline = re.compile(r'Duration\s*:\s*Ys/\s*Ms/\s*Ds/\s*\n\s*(\d{2})\s+(\d{2})\s+(\d{2})', re.IGNORECASE)
        duration_pattern_singleline = re.compile(r'DURATION\s*:\s*(\d+)(?:Ys|Y)[.\s]*(\d+)(?:Ms|M)[.\s]*(\d+)(?:Ds|D)[.\s]*', re.IGNORECASE)

         # Pattern to match 'DURATION : 3Ys.3Ms.2Ds.' format
        pattern_duration_uppercase = re.compile(r'DURATION\s*:\s*(\d+)(?:Ys|Y)[.\s]*(\d+)(?:Ms|M)[.\s]*(\d+)(?:Ds|D)[.\s]*', re.IGNORECASE)
        pattern_duration_colon = re.compile(r'Duration:\s*(\d+)\s*Ys[.\s]*(\d+)\s*Ms[.\s]*(\d+)\s*Ds', re.IGNORECASE)
        pattern_duration_combined = re.compile(r'(\d+)\s*Ys?[.\s]*(\d+)\s*Ms?[.\s]*(\d+)\s*Ds?|(\d+)\s*[Yy][.\s]*(\d{2})\s*[Mm][.\s]*(\d{2})\s*[Dd]s?', re.IGNORECASE)

        # Flexible pattern to match various formats, including negative values for months
        pattern_duration_flexible = re.compile(r'DURATION\s*:\s*(-?\d+)\s*(?:Ys?\.?|Y\.?)\s*(-?\d*)\s*(?:Ms?\.?|M\.?)\s*(-?\d*)\s*(?:Ds?\.?|D\.?)', re.IGNORECASE)

        # Regular expression to extract years, months, and days

        pattern_duration_flexible2 = re.compile(r'--Y\.(\d+)Ms\.(\d+)Ds\.')
        pattern_duration_flexible1 = re.compile(r'Duration\s*Ys\.\s*Ms\.\s*Ds\.\s*(\d+)\s*(\d*)\s*(\d*)', re.IGNORECASE )

        #pattern_duration_colon1 = re.compile(r'Duration: :\s*(\d+)\s*Y[.\s]*(\d{2})\s*M[.\s]*(\d{2})\s*Ds', re.IGNORECASE)

        # Search for each date

        received_on_match = received_or_presented_on_pattern.search(cleaned_text)
        received_on_match1 = received_or_presented_on_pattern1.search(cleaned_text)
        registered_on_match = registered_on_pattern.search(cleaned_text)
        decided_on_match = decided_on_pattern.search(cleaned_text)
        # Extract dates
        received_on = received_on_match.group(1) if received_on_match else received_on_match1.group(1) if received_on_match1 else " "
        registered_on = registered_on_match.group(1) if registered_on_match else " "
        decided_on = decided_on_match.group(1) if decided_on_match else " "
 
        def extract_durations(cleaned_text):
            # Check if the word "Duration:" is present in the input text
            if "Duration :" in cleaned_text:
                # Extract all numbers following "Duration:" from the input text
                numbers = [int(match) for match in re.findall(r'\b(\d+)\b', cleaned_text.split("Duration :")[1])]
                # Initialize years, months, and days
                years = numbers[0] if len(numbers) > 0 else 0
                months = numbers[1] if len(numbers) > 1 else 0
                days = numbers[2] if len(numbers) > 2 else 0
                duration = f"{years} years, {months} months, {days} days"
                return duration

            else:

                return " "


        # Extract durations

        duration_match_multiline = duration_pattern_multiline.search(cleaned_text)
        duration_match_singleline = duration_pattern_singleline.search(cleaned_text)
        match_duration_uppercase = pattern_duration_uppercase.search(cleaned_text)
        pattern_duration_colon = pattern_duration_colon.search(cleaned_text)
        match_duration_combined = pattern_duration_combined.search(cleaned_text)

        # Extract durations based on the flexible pattern
        match_duration_flexible = pattern_duration_flexible.search(cleaned_text)
        # Extract durations based on the flexible pattern
        match_duration_flexible1 = pattern_duration_flexible1.search(cleaned_text)
        # Search for the pattern in the line
        match_duration_flexible2 = pattern_duration_flexible2.search(cleaned_text)
        if duration_match_multiline:
            years, months, days = duration_match_multiline.groups()
            duration = f"{years} years, {months} months, {days} days"
        elif duration_match_singleline:
            years, months, days = duration_match_singleline.groups()
            duration = f"{years} years, {months} months, {days} days"

        elif match_duration_uppercase:
            years, months, days = match_duration_uppercase.groups()
            duration = f"{years} years, {months} months, {days} days"

        elif pattern_duration_colon:
            years, months, days = pattern_duration_colon.groups()
            duration = f"{years} years, {months} months, {days} days"
        elif match_duration_combined:
            groups = [group for group in match_duration_combined.groups() if group is not None]
            years, months, days = map(int, groups)
            duration = f"{years} years, {months} months, {days} days"

        elif match_duration_flexible:
            years, months, days = match_duration_flexible.groups()
            # Handle cases where years or days might be empty
            years = 0 if not years or years == '-' or years == '--' else int(years)
            months = 0 if not months or months == '-' else int(months)
            days = 0 if not days or  days == '-' else int(days)
            duration = f"{years} years, {months} months, {days} days"

        elif match_duration_flexible1:
            years, months, days = match_duration_flexible1.groups() 
            # Handle cases where years or days might be empty
            years = 0 if not years else int(years)
            months = 0 if not months else int(months)
            days = 0 if not days else int(days)
            duration = f"{years} years, {months} months, {days} days"
            # Check if a match is found and extract values

        elif match_duration_flexible2:
            months = int(match_duration_flexible2.group(1))
            days = int(match_duration_flexible2.group(2))
            years = 0
            duration = f"{years} years, {months} months, {days} days" 
        else:
            duration = extract_durations(cleaned_text)
            print(duration)

        # Case Number
        case_number_pattern = re.compile(

            r'M\.?A\.?C\.?P\.?\s*No\.?\s*(\d+)(?:\/(\d+))?',

            re.IGNORECASE

        )

        case_number_match = case_number_pattern.search(cleaned_text)

        if case_number_match:

            # Construct the case number from the matched groups

            case_number = "MACP No." + case_number_match.group(1)

            if case_number_match.group(2):

                case_number += "/" + case_number_match.group(2)

        else:

            case_number = ""

        # CNR Number

        cnr_number_pattern = re.compile(

            r'(?:CNR No\.?|CNR)\s*:? MHPU\d{2}-?\s*0?\d{3,6}-\d{4}|MHPU\d{2}\D*\d{6}\D*\d{4}|MHPU\d{2}-?\d{3,6}-\d{4}',

            re.IGNORECASE

            #.replace("\xad", "")
 
        )

        cnr_number_match = cnr_number_pattern.search(cleaned_text)
        if cnr_number_match:
            cnr_number = cnr_number_match.group(0).replace("CNR No. ", "").replace("CNR No", "").replace("CNR ", "").replace("\n", "").replace(" ", "")
        else:
            cnr_number = ""

        #Court Title
        court_title_pattern = re.compile(

            r'BEFORE THE (NATIONAL LOK-ADALAT, HELD AT PUNE|MEMBER, MOTOR ACCIDENT CLAIMS\s+TRIBUNAL, PUNE AT PUNE)',

            re.IGNORECASE | re.DOTALL

        )

        court_title_match = court_title_pattern.search(cleaned_text)

        if court_title_match:

            court_title = court_title_match.group(0).strip()

        else:

            court_title = ""


        # Judge Name

        judge_name_pattern = re.compile(r'Digitally signed by (.+?) Date:')

        judge_name_match = judge_name_pattern.search(cleaned_text)

        judge_name = judge_name_match.group(1).strip() if judge_name_match else ""

        old_claim_pattern = re.compile(r'Claim Application under Section\s+(\d+)\s+of the Motor Vehicles Act')

        old_claim_match = old_claim_pattern.search(cleaned_text)

        # New Claim Under Section pattern (for Legal Services Authority Act, 1987)

        new_claim_pattern = re.compile(r'Pune under Section (\d+) of the Legal Services Authority Act, 1987')

        new_claim_match = new_claim_pattern.search(cleaned_text)

        # Determine which pattern matches and use that

        if old_claim_match:

            claim_info = f"Section {old_claim_match.group(1)} of the Motor Vehicles Act"

        elif new_claim_match:

            claim_info = f"Section {new_claim_match.group(1)} of the Legal Services Authority Act, 1987"

        else:

            claim_info = ""

        # Brief Description of the Accident

        accident_description_pattern = re.compile(r'The petition in short, is as under\s*:\s*(.*?)(?=\. On)', re.DOTALL)

        accident_description_match = accident_description_pattern.search(cleaned_text)

        accident_description = accident_description_match.group(1).strip() if accident_description_match else ""

        # Date of Accident

        date_pattern = re.compile(r'which took place on (\d{2}\.\d{2}\.\d{4})')

        date_match = date_pattern.search(cleaned_text)

        accident_date = date_match.group(1).strip() if date_match else ""

        # Place of Accident

        place_pattern = re.compile(r'on\s([^\,\.]+? road in [^\,\.]+)(?:\.|\,)|in front of ([^\,\.]+), near [^\,\.]+, ([^\,\.]+)', re.IGNORECASE)
        place_match = place_pattern.search(cleaned_text)
        if place_match:
            if place_match.group(1):
                accident_place = place_match.group(1).strip()
            else:
                accident_place = place_match.group(2).strip() + ", " + place_match.group(3).strip()
        else:
            accident_place = ""

        # Death/Injury Details
        death_injury_pattern = re.compile(r'(deceased was seriously injured and succumbed to injuries|account of accidental death of [\w\s]+)', re.IGNORECASE)
        death_injury_match = death_injury_pattern.search(cleaned_text)
        death_injury_details = death_injury_match.group(0) if death_injury_match else ""

        # Registration No of vehicle 1
        registration_pattern = re.compile(r'registration No\.?\s*([A-Z]{2}-?\s?[0-9]{2}-?\s?[A-Z]*-?\s?[0-9]{4})',re.IGNORECASE)
        registration_match = registration_pattern.search(cleaned_text)
        registration_number = registration_match.group(1).strip() if registration_match else ""

        # Deceased/Victim Name
        name_pattern = re.compile(r'Deceased\s+([A-Za-z]+(?:\s+[A-Za-z]+){0,2})', re.IGNORECASE)
        deceased_names = name_pattern.findall(cleaned_text)
        if deceased_names:
            cleaned_deceased_name = deceased_names[0].strip()
        else:
            cleaned_deceased_name = ""

        # Deceased/Victim Age
        age_pattern = re.compile(r'age(?:d)?\s+(\d+)(?:\s+years(?:\s+old)?)?', re.IGNORECASE)
        age_match = age_pattern.search(cleaned_text)
        deceased_victim_age = age_match.group(1) if age_match else ""

        # Deceased/Victim Income
        income_pattern = re.compile(r'(?:earning|salary)\s+Rs\.\s*([0-9,/-]+)(?:\s+per month|\s+monthly)?', re.IGNORECASE)
        income_match = income_pattern.search(cleaned_text)
        deceased_victim_income = income_match.group(1) if income_match else ""

        # Deceased/Victim's Occupation
        occupation_pattern = re.compile(r'worked in ([\w\s]+) as ([\w\s]+)')
        occupation_match = occupation_pattern.search(cleaned_text)
        if occupation_match:
            company = occupation_match.group(1).strip()
            position = occupation_match.group(2).strip()
            deceased_victim_occupation = f"{position} at {company}"
        else:
            deceased_victim_occupation = ""

        # Account Number
        account_number_pattern = re.compile(r'Account Number\s*[-:]*\s*(\d+)', re.IGNORECASE)
        account_number_match = account_number_pattern.search(cleaned_text)
        account_number = account_number_match.group(1).strip() if account_number_match else ""
        print(account_number)
        account_name_pattern = re.compile(r'Account Name\s*[-:]\s*([-\w\s,]+)',re.IGNORECASE)
        account_name_match = account_name_pattern.search(cleaned_text)
        account_name = account_name_match.group(1).strip() if account_name_match else ""
        print(account_name)

        # Bank Name

        #bank_name_pattern = re.compile(r'Name of Bank\s*(.*?)(?:\.|, IFSC Code)', re.IGNORECASE | re.DOTALL)

        #bank_name_pattern = re.compile(r'(State Bank of India),\s*(\w+)\s+Court Branch,\s*(Pune)', re.IGNORECASE)
        bank_name_pattern = re.compile(r'(State Bank of India),\s*(\w+)\s+Court Branch,\s*(Pune)|Name of Bank\s*[-:]\s*(.*?),\s*(.*?)\s+Court Branch,\s*(\w+)',re.IGNORECASE)
        bank_name_match = bank_name_pattern.search(cleaned_text)
        if bank_name_match:
            bank_name = bank_name_match.group(1).strip() if bank_name_match else ""
            print(bank_name)
        else:
            bank_name = ""
            print("Bank name not found in the text")
            #bank_name = bank_name_match.group(1).strip() if bank_name_match else ""
        print(bank_name_match)

        # IFSC Code
        ifsc_code_pattern = re.compile(r'IFSC Code\s*[-:]*\s*(SBIN\d{6})',re.IGNORECASE)
        ifsc_code_match = ifsc_code_pattern.search(cleaned_text)
        ifsc_code = ifsc_code_match.group(1).strip() if ifsc_code_match else ""

        # Claim Rs.
        claim_pattern = re.compile(r'Claim Rs\.\s*([\d,/-]+)')
        claim_match = claim_pattern.search(cleaned_text)
        claim_amount = claim_match.group(1).strip() if claim_match else ""

        # Advocate for Applicants
        advocate_pattern = re.compile(r'Advocate for Applicants\s*:\s*([\w\s.]+?)(?=,\s*Shri\.|For opponent|$)',re.IGNORECASE | re.DOTALL)
        advocate_match = advocate_pattern.search(cleaned_text)
        advocate_name = advocate_match.group(1).strip() if advocate_match else ""

        # Advocate for opponent No.1
        advocate_opponent1_pattern = re.compile(r'Advocate for opponent No\.1\s*:\s*(.*?)(?=\s*Advocate for opponent No\. 2)', re.IGNORECASE | re.DOTALL)
        advocate_opponent1_match = advocate_opponent1_pattern.search(cleaned_text)
        advocate_opponent1_name = advocate_opponent1_match.group(1).strip() if advocate_opponent1_match else ""

        # Advocate for opponent No.2
        advocate_opponent2_pattern = re.compile(r'Advocate for opponent No\. 2\s*:\s*((?:Shri\.?\s+[A-Z]\.\s+[A-Z]\.\s+\w+)(?:\s*,\s*(?:Shri\.?\s+[A-Z]\.\s+[A-Z]\.\s+\w+))*)', re.IGNORECASE | re.DOTALL)
        advocate_opponent2_match = advocate_opponent2_pattern.search(cleaned_text)
        advocate_opponent2_name = advocate_opponent2_match.group(1).strip() if advocate_opponent2_match else ""

        # Name of Steno
        steno_pattern = re.compile(r'Name of Steno : (.+?) Date of order')
        steno_match = steno_pattern.search(cleaned_text)
        steno_name = steno_match.group(1).strip() if steno_match else ""

        # Order uploaded on
        order_uploaded_pattern = re.compile(r'Order uploaded on : (\d{2}\.\d{2}\.\d{4})')
        order_uploaded_match = order_uploaded_pattern.search(cleaned_text)
        order_uploaded_date = order_uploaded_match.group(1).strip() if order_uploaded_match else ""

        # Date of Order
        date_of_order_pattern = re.compile(r'Date of order : (\d{2}\.\d{2}\.\d{4})')
        date_of_order_match = date_of_order_pattern.search(cleaned_text)
        date_of_order = date_of_order_match.group(1).strip() if date_of_order_match else ""
        
        insurance_company_pattern = re.compile(r'\b(?:[A-Za-z]+\s)*(?:Insurance|Insurer|Ltd\.|Limited|Corporation|Corp\.|Company|Co\.|Group)\b',re.IGNORECASE)
        insurance_company_match = insurance_company_pattern.search(cleaned_text)
        insurance_company_name = insurance_company_match.group(0).strip() if insurance_company_match else " "
        
        medical_expenses_pattern = re.compile(r'Medical expenses Rs\.\s*([\d,/-]+)',re.IGNORECASE)
        medical_expenses_match = medical_expenses_pattern.search(cleaned_text)
        medical_expenses = medical_expenses_match.group(1).strip() if medical_expenses_match else " "

        fir_number_pattern = re.compile(r'FIR Exh\.\s*(\d+)',re.IGNORECASE)
        fir_number_match = fir_number_pattern.search(cleaned_text)
        fir_number = fir_number_match.group(1).strip() if fir_number_match else " "

        police_station_pattern = re.compile(r'Police Station,\s*([A-Za-z ]+)',re.IGNORECASE)
        police_station_match = police_station_pattern.search(cleaned_text)
        police_station_name = police_station_match.group(1).strip() if police_station_match else " "

        hospital_pattern = re.compile(r'(?:First hospital details\s+)?([A-Za-z ]+ Hospital)\s*(?:,|\b)(?:\s*Second hospital details\s+([A-Za-z ]+ Hospital))?',re.IGNORECASE)
        hospital_match = hospital_pattern.search(cleaned_text)
        first_hospital = hospital_match.group(1).strip() if hospital_match and hospital_match.group(1) else " "
        second_hospital = hospital_match.group(2).strip() if hospital_match and hospital_match.group(2) else None
        
        applicant_data = extract_applicants(cleaned_text, first_two_pages_text)
        opponent_data = extract_opponents(cleaned_text, first_two_pages_text)


        written_statement_pattern = re.compile(r'(Exh\.\s*\d+\s+(?:opponent\s*No\.?1|respondent)\s+filed\s+written\s+statement)(.*?)(?=Exh\.|\Z)',re.IGNORECASE)
        written_statement_match = written_statement_pattern.findall(cleaned_text)
        written_statement_content = " ".join([match[1].strip() for match in written_statement_match])
        
        written_statement_opponent2_pattern = re.compile(r'(Exh\.\s*\d+\s+opponent\s*No\.?2\s+filed\s+written\s+statement)(.*?)(?=Exh\.|\Z)',re.IGNORECASE | re.DOTALL)
        written_statement_opponent2_matches = written_statement_opponent2_pattern.findall(cleaned_text)
        written_statement_opponent2_content = " ".join([match[1].strip() for match in written_statement_opponent2_matches])

        judgment_date_pattern = re.compile(r'Delivered on (?:this )?(\d{1,2})(?:st|nd|rd|th)?\s+Day of (\w+)\s+(\d{4})', re.IGNORECASE)
        judgment_date_match = judgment_date_pattern.search(cleaned_text)
        if judgment_date_match:
            day, month, year = judgment_date_match.groups()
            judgment_date = f"{day} {month} {year}"
        else:
            judgment_date = ""


        marital_status_pattern = re.compile(r'Deceased\s+(?:was\s+)?(married|bachelor)', re.IGNORECASE)
        marital_status_match = marital_status_pattern.search(cleaned_text)
        if marital_status_match:
            marital_status = marital_status_match.group(1)
        else:
            marital_status = " "

        witness_no_1_pattern = re.compile(r'([A-Za-z\s.]+)\s+is\s+examined\s+as\s+witness\s+No\.?\s*1', re.IGNORECASE)
        # Search for witness No. 1 in the text
        witness_no_1_match = witness_no_1_pattern.search(cleaned_text)

        # Extract the witness number
        witness_no_1 = witness_no_1_match.group() if witness_no_1_match else ""  
        witness_no_2_pattern = re.compile(r'([A-Za-z\s.]+)\s+as\s+witness\s+No\.?\s*2', re.IGNORECASE)

        # Search for witness No. 2 in the text
        witness_no_2_match = witness_no_2_pattern.search(cleaned_text)

        # Extract the witness number
        witness_no_2 = witness_no_2_match.group() if witness_no_2_match else ""


        # Interest Rate
        interest_rate = ""
        phrases_to_check = ['interest on the total compensation', 'interest', 'amount at the rate of']
        for phrase in phrases_to_check:
            if phrase in cleaned_text:
                received_on_index = cleaned_text.find(phrase)
                if received_on_index != -1:
                    received_on_content = cleaned_text[received_on_index + len(phrase):].strip()
                    interest_rate_match = re.search(r'@ (\d+(\.\d+)?)% per annum', received_on_content)
                    if interest_rate_match:
                        interest_rate = interest_rate_match.group(1)
                        break  # Break the loop once interest rate is found

        # Create a dictionary to hold the extracted information
        info_dict = {col: "" for col in all_columns}
        info_dict = {
            "File Name": pdf_file,
            "RECEIVED ON": received_on,
            "REGISTERED ON": registered_on,
            "DECIDED ON": decided_on,
            "DURATION": duration,
            "Case Number": case_number,
            "CNR Number": cnr_number,
            "Court Title": court_title,
            "Judge Name": judge_name,
            "Claim Under Section": claim_info,
            "Brief Description of the Accident": accident_description,
            "Date of Accident": accident_date,
            "Place of Accident": accident_place,
            "Death/Injury Details": death_injury_details,
            "Registration No of vehicle 1": registration_number,
            "Deceased/Victim Name": cleaned_deceased_name,
            "Deceased/Victim Age": deceased_victim_age,
            "Deceased/Victim Income": deceased_victim_income,
            "Deceased/Victim's Occupation": deceased_victim_occupation,
            "Account Number": account_number,
            "Account_Name" : account_name,

            #"Bank Name": bank_name,

            "IFSC Code": ifsc_code,
            "Claim Rs.": claim_amount,
            "Advocate for Applicants": advocate_name,
            "Advocate for opponent No.1": advocate_opponent1_name,
            "Advocate for opponent No.2": advocate_opponent2_name,
            "Name of Steno": steno_name,
            "Order uploaded on": order_uploaded_date,
            "Date of Order": date_of_order,
            "Insurance company name":insurance_company_name,
            "Medical expenses":medical_expenses,
            "Fir number":fir_number,
            "Police station name":police_station_name,
            "First hospital name":first_hospital,
            "Second hospital name":second_hospital,
            "Written Statement by Opponent No.1":written_statement_content,
            "Written Statement by Opponent No.2":written_statement_opponent2_content,
            "Judgment Date" : judgment_date,
            "Deceased Marital Status" : marital_status,
            "Witness No 1 " : witness_no_1,
            "Witness No 2 "  : witness_no_2,
            "Interest Rate": interest_rate
        }

        info_dict.update(applicant_data)
        info_dict.update(opponent_data)
        print(f"eachfile{info_dict}")

        # Append the information to a list of DataFrames
        dfs = [df, pd.DataFrame([info_dict])]
        df = pd.concat(dfs, ignore_index=True)
        print(df)
    return df

def unique_file_with_timestamp(base_path, suffix='.xlsx'):
    """Generate a unique file path with a timestamp, appending numbers if necessary."""

    timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")
    counter = 1
    new_path = f"{base_path}_{timestamp}{suffix}"
    while os.path.exists(new_path):
        new_path = f"{base_path}_{timestamp}_{counter}{suffix}"
        counter += 1
    return new_path
 
 


# Example usage
folder_path = r"D:\Bajaj\Structured PDF"  # Replace with your folder path
df = pd.DataFrame(columns=all_columns)
result_df = process_pdfs_in_folder(folder_path, df)
 
 
# Find a unique filename with timestamp and save the DataFrame
base_filename = "Downloads"  # Base path for the file
unique_filename = unique_file_with_timestamp(base_filename)
result_df.to_excel(unique_filename, index=False)

 
# Print success message
print(f"File exported successfully as '{unique_filename}'")

Processing MACP 1 2020.pdf...
Presented on : 07/01/2020 Registered on : 07/01/2020 Decided on : 01/12/2022 Duration : Ys/ Ms/ Ds/ 02 11 23 BEFORE THE MEMBER, MOTOR ACCIDENT CLAIMTRIBUNAL, PUNE AT ­ PUNE. ( Presided over by Shri. S.B. Hedaoo) Motor Accident Claim Petition No. 01/2020 CNR NO : MHPU01­000424­2020 Exh. No. 1] Smt. Vanita Balbhim Rupnur Age : 20 years, Occ. Household, R/at – Wadki, Tal Haveli, Dist Pune. 2] Mrs. Sundrabai Shrimant Karnure Age : 55 years, Occu : Household, 3] Mr. Shirmant Nagnath Karnure Age : 60 yrs., Occu – Nil, R/at : Nai Chakur, Umarga, Osmanabad. ….Applicant Vs. 1] Mr. Rama Babu Kudaskar Age : 56 yrs., Occu : Business, R/at : H.No. 32, Wathadev Karapur, Bicholim, Sankhalim, North Goa – 403 506. 2] The Manager, Bajaj Allianz General Insurance Co. Ltd., Off – 'Vardhman', 7 Loves Chowk, Shankarsheth Road, Pune – 411 042. ....Opponent Claim of Rs. 35,00,000/­ MACP No. 01/2020 2 CNR No. MHPU01­000424­2020 Judgment Appearances :­ Adv. Sanjay Raut, for the app

2 years, 11 months, 23 days


{}
eachfile{'File Name': 'MACP 1 2020.pdf', 'RECEIVED ON': '07/01/2020', 'REGISTERED ON': '07/01/2020', 'DECIDED ON': '01/12/2022', 'DURATION': '2 years, 11 months, 23 days', 'Case Number': 'MACP No.01/2020', 'CNR Number': 'MHPU01\xad000424\xad2020', 'Court Title': '', 'Judge Name': 'SACHIDANAND BAPURAO HEDAOO', 'Claim Under Section': '', 'Brief Description of the Accident': '', 'Date of Accident': '', 'Place of Accident': '', 'Death/Injury Details': '', 'Registration No of vehicle 1': '', 'Deceased/Victim Name': 'Sandip Shrimant Karunure', 'Deceased/Victim Age': '', 'Deceased/Victim Income': '', "Deceased/Victim's Occupation": '', 'Account Number': '', 'Account_Name': '', 'IFSC Code': '', 'Claim Rs.': '', 'Advocate for Applicants': '', 'Advocate for opponent No.1': '', 'Advocate for opponent No.2': '', 'Name of Steno': '', 'Order uploaded on': '', 'Date of Order': '', 'Insurance company name': 'Bajaj Allianz General Insurance', 'Medical expenses': ' ', 'F

41365622240

{'Applicant 1 Number': '1', 'Applicant 1 Name': 'Smt. Chhaya Ganesh Kasbe', 'Applicant 1 Age': '35', 'Applicant 1 Occupation': 'Household', 'Applicant 1 Address': 'o Laxminagar, Yerwada, Pune.\n ...', 'Applicant 2 Number': '2', 'Applicant 2 Name': 'Hrishikesh Ganesh Kasbe', 'Applicant 2 Age': '14', 'Applicant 2 Occupation': 'Student', 'Applicant 2 Address': '', 'Applicant 3 Number': '3', 'Applicant 3 Name': 'Arushi Ganesh Kasbe', 'Applicant 3 Age': '12', 'Applicant 3 Occupation': 'Student', 'Applicant 3 Address': '', 'Applicant 4 Number': '4', 'Applicant 4 Name': 'Bhimrao Pandhari Kasbe', 'Applicant 4 Age': '65', 'Applicant 4 Occupation': 'labour', 'Applicant 4 Address': ''}
eachfile{'File Name': 'MACP 1 2021.pdf', 'RECEIVED ON': '20.12.2020', 'REGISTERED ON': '05.01.2021', 'DECIDED ON': '24.04.2023', 'DURATION': '2 years, 3 months, 20 days', 'Case Number': 'MACP No.1/2021', 'CNR Number': 'MHPU01-014037-2020', 'Court Title': 'BEFORE THE MEMBER, MOTOR ACCIDENT CLAIMS TRIBUN

41365622240

{'Applicant 1 Number': '1', 'Applicant 1 Name': 'Mini Shaju', 'Applicant 1 Age': '43', 'Applicant 1 Occupation': 'Housewife.', 'Applicant 1 Address': '', 'Applicant 2 Number': '2', 'Applicant 2 Name': 'Nisha Shaju', 'Applicant 2 Age': '21', 'Applicant 2 Occupation': 'Education', 'Applicant 2 Address': ''}
eachfile{'File Name': 'MACP 117 2020.pdf', 'RECEIVED ON': '03.02.2020', 'REGISTERED ON': '06.03.2020', 'DECIDED ON': '01.09.2023', 'DURATION': '3 years, 5 months, 27 days', 'Case Number': 'MACP No.117/2020', 'CNR Number': 'MHPU01-004422-2020', 'Court Title': 'BEFORE THE MEMBER, MOTOR ACCIDENT CLAIMS TRIBUNAL, PUNE AT PUNE', 'Judge Name': 'BHUSHAN PRAKASH KSHIRSAGAR', 'Claim Under Section': 'Section 166 of the Motor Vehicles Act', 'Brief Description of the Accident': '', 'Date of Accident': '07.10.2019', 'Place of Accident': '', 'Death/Injury Details': 'account of accidental death of Shaju Thankachan', 'Registration No of vehicle 1': 'MH-12-DT-4963', 'Deceased/Victim Name'



{}
eachfile{'File Name': 'MACP 12 2020.pdf', 'RECEIVED ON': '07.12.2019', 'REGISTERED ON': '02.01.2020', 'DECIDED ON': '25.11.2022', 'DURATION': '2 years, 1 months, 23 days', 'Case Number': 'MACP No.12/2020', 'CNR Number': 'MHPU010005722020', 'Court Title': '', 'Judge Name': '', 'Claim Under Section': '', 'Brief Description of the Accident': '', 'Date of Accident': '', 'Place of Accident': '', 'Death/Injury Details': '', 'Registration No of vehicle 1': 'MH-12-HV-1820', 'Deceased/Victim Name': '', 'Deceased/Victim Age': '', 'Deceased/Victim Income': '', "Deceased/Victim's Occupation": '', 'Account Number': '', 'Account_Name': '', 'IFSC Code': '', 'Claim Rs.': '', 'Advocate for Applicants': '', 'Advocate for opponent No.1': '', 'Advocate for opponent No.2': '', 'Name of Steno': '', 'Order uploaded on': '', 'Date of Order': '', 'Insurance company name': 'for repairs and informed about damages to the insurance company', 'Medical expenses': ' ', 'Fir number': ' ', 'Police station name': '

...

0 years, 11 months, 0 days
41365622240
Member, Motor Accident Claim Tribunal, Pune
{}
eachfile{'File Name': 'MACP 631 2022.pdf', 'RECEIVED ON': '28/11/2022', 'REGISTERED ON': '01/12/2022', 'DECIDED ON': '31/10/2023', 'DURATION': '0 years, 11 months, 0 days', 'Case Number': 'MACP No.631/2022', 'CNR Number': 'MHPU010238822022', 'Court Title': '', 'Judge Name': 'SACHIDANAND BAPURAO HEDAOO', 'Claim Under Section': '', 'Brief Description of the Accident': '', 'Date of Accident': '', 'Place of Accident': '', 'Death/Injury Details': '', 'Registration No of vehicle 1': 'MH-12- GL-5894', 'Deceased/Victim Name': 'Satish Punekar was', 'Deceased/Victim Age': '62', 'Deceased/Victim Income': '', "Deceased/Victim's Occupation": '', 'Account Number': '41365622240', 'Account_Name': 'Member, Motor Accident Claim Tribunal, Pune', 'IFSC Code': 'SBIN006157', 'Claim Rs.': '', 'Advocate for Applicants': '', 'Advocate for opponent No.1': '', 'Advocate for opponent No.2': '', 'Name of Steno': '', 'Order upload

0 years, 8 months, 13 days


{}
eachfile{'File Name': 'MACP 649 2022.pdf', 'RECEIVED ON': '05/12/2022', 'REGISTERED ON': '07/12/2022', 'DECIDED ON': '19/08/2023', 'DURATION': '0 years, 8 months, 13 days', 'Case Number': 'MACP No.648/2022', 'CNR Number': 'MHPU01\xad024277\xad2022', 'Court Title': '', 'Judge Name': 'SACHIDANAND BAPURAO HEDAOO', 'Claim Under Section': '', 'Brief Description of the Accident': '', 'Date of Accident': '', 'Place of Accident': '', 'Death/Injury Details': '', 'Registration No of vehicle 1': '', 'Deceased/Victim Name': 'boy was riding', 'Deceased/Victim Age': '8', 'Deceased/Victim Income': '', "Deceased/Victim's Occupation": '', 'Account Number': '', 'Account_Name': '', 'IFSC Code': '', 'Claim Rs.': '', 'Advocate for Applicants': '', 'Advocate for opponent No.1': '', 'Advocate for opponent No.2': '', 'Name of Steno': '', 'Order uploaded on': '', 'Date of Order': '', 'Insurance company name': 'HDFC ERGO General Insurance', 'Medical expenses': ' ', 'Fir number': 



{}
eachfile{'File Name': 'MACP 68 2020.pdf', 'RECEIVED ON': '10.01.2020', 'REGISTERED ON': '30.01.2020', 'DECIDED ON': '02.05.2023', 'DURATION': '3 years, 4 months, 28 days', 'Case Number': 'MACP No.68/2020', 'CNR Number': 'MHPU010033222020', 'Court Title': '', 'Judge Name': '', 'Claim Under Section': '', 'Brief Description of the Accident': '', 'Date of Accident': '', 'Place of Accident': '', 'Death/Injury Details': '', 'Registration No of vehicle 1': 'MH-22-U- 9080', 'Deceased/Victim Name': 'Swati Kumbharkar was', 'Deceased/Victim Age': '33', 'Deceased/Victim Income': '10,000/-', "Deceased/Victim's Occupation": '', 'Account Number': '', 'Account_Name': '', 'IFSC Code': '', 'Claim Rs.': '', 'Advocate for Applicants': '', 'Advocate for opponent No.1': '', 'Advocate for opponent No.2': '', 'Name of Steno': '', 'Order uploaded on': '', 'Date of Order': '', 'Insurance company name': 'Cholamandalam MS General Insurance', 'Medical expenses': ' ', 'Fir number': ' ', 'Police station name': 

1 years, 8 months, 7 days


{}
eachfile{'File Name': 'MACP 80 2022.pdf', 'RECEIVED ON': '04/02/2022', 'REGISTERED ON': '22/02/2022', 'DECIDED ON': '11/10/2023', 'DURATION': '1 years, 8 months, 7 days', 'Case Number': 'MACP No.80/2022', 'CNR Number': 'MHPU010034482022', 'Court Title': '', 'Judge Name': 'MOHAN GULABRAO CHAVAN', 'Claim Under Section': '', 'Brief Description of the Accident': '', 'Date of Accident': '', 'Place of Accident': '', 'Death/Injury Details': '', 'Registration No of vehicle 1': '', 'Deceased/Victim Name': '', 'Deceased/Victim Age': '', 'Deceased/Victim Income': '', "Deceased/Victim's Occupation": '', 'Account Number': '', 'Account_Name': '', 'IFSC Code': 'SBIN006157', 'Claim Rs.': '', 'Advocate for Applicants': '', 'Advocate for opponent No.1': '', 'Advocate for opponent No.2': '', 'Name of Steno': '', 'Order uploaded on': '', 'Date of Order': '', 'Insurance company name': 'he was employee of Birani Group', 'Medical expenses': ' ', 'Fir number': ' ', 'Police stati

3 years, 6 months, 18 days


{}
eachfile{'File Name': 'MACP 99 2020.pdf', 'RECEIVED ON': '03/02/2020', 'REGISTERED ON': '04/03/2020', 'DECIDED ON': '21/09/2023', 'DURATION': '3 years, 6 months, 18 days', 'Case Number': 'MACP No.99/2020', 'CNR Number': 'MHPU01\xad004268\xad2020', 'Court Title': '', 'Judge Name': 'SACHIDANAND BAPURAO HEDAOO', 'Claim Under Section': '', 'Brief Description of the Accident': '', 'Date of Accident': '', 'Place of Accident': '', 'Death/Injury Details': '', 'Registration No of vehicle 1': '', 'Deceased/Victim Name': '', 'Deceased/Victim Age': '53', 'Deceased/Victim Income': '', "Deceased/Victim's Occupation": '', 'Account Number': '', 'Account_Name': '', 'IFSC Code': '', 'Claim Rs.': '', 'Advocate for Applicants': '', 'Advocate for opponent No.1': '', 'Advocate for opponent No.2': '', 'Name of Steno': '', 'Order uploaded on': '', 'Date of Order': '', 'Insurance company name': 'Bajaj Allianz General Insurance Company', 'Medical expenses': ' ', 'Fir number': '22

# Updated

In [1]:
import os
import fitz  # PyMuPDF
import re
import pandas as pd
import spacy

# Load SpaCy model
nlp = spacy.load("en_core_web_sm")
import os
from datetime import datetime

# Define an empty DataFrame with the desired column names
initial_columns  = ["File Name", "RECEIVED ON", "REGISTERED ON", "DECIDED ON", "DURATION", "Case Number", "CNR Number",
            "Court Title", "Judge Name", "Claim Under Section", "Brief Description of the Accident",
           "Date of Accident", "Place of Accident", "Death/Injury Details", "Registration No of vehicle 1",
           "Deceased/Victim Name", "Deceased/Victim Age", "Deceased/Victim Income", "Deceased/Victim's Occupation",
           "Account Number", "Bank Name", "IFSC Code", "Claim Rs.", "Advocate for Applicants",
           "Advocate for opponent No.1", "Advocate for opponent No.2", "Name of Steno", "Order uploaded on",
           "Date of Order","Insurance company name","Medical expenses","Police station name","First hospital name",
           "Second hospital name","Interest Rate"]

# Assuming the maximum number of individual and organization opponents

max_opponents_individual = 5
max_opponents_organization = 5

# Define opponent individual columns

opponent_individual_columns = []
for i in range(1, max_opponents_individual + 1):
    opponent_individual_columns.extend([
        f"Opponent {i} Number", f"Opponent {i} Name", f"Opponent {i} Age",
        f"Opponent {i} Occupation", f"Opponent {i} Address"])

# Define opponent organization columns
opponent_organization_columns = []
for i in range(1, max_opponents_organization + 1):
    opponent_organization_columns.extend([
        f"Opponent Org {i} Number", f"Opponent Org {i} Name", f"Opponent Org {i} Address"])

# Combine all columns
all_columns = initial_columns + opponent_individual_columns
df = pd.DataFrame(columns=all_columns)
def extract_and_clean_text_from_pdf(pdf_path):
    # Open the PDF file
    doc = fitz.open(pdf_path)
    text = ""
    for page in doc:
        text += page.get_text()
    doc.close()

    # Clean the extracted text
    cleaned_text = re.sub(r'\s+', ' ', text)  # Remove unwanted spaces
    cleaned_text = cleaned_text.strip()  # Remove leading and trailing spaces
    print(cleaned_text)
    return cleaned_text

def extract_applicants(cleaned_text, first_two_pages_text):
    # Updated regular expression patterns
    detailed_pattern= re.compile(r'(\d+)-\s*(Mrs\.|Mr\.|Smt\.|Miss)?\s*([\w\s.]+?)\s+Age\s+(\d+)\s+years,\s+Occ\s*:\s*([^\n,]+)(?:,\s+)?(?:Both\s+R\/?at\s+|R\/?o\s+)?([\w\s,.-]*?)\s*\.*\s*(?:\.\.\.)?\s*Applicants?.*?(?=Versus|v\/s|V\/s|v \/ s|V \/ s|versus)',re.IGNORECASE | re.DOTALL)
    simple_pattern = re.compile( r'(\d+)-\s*(?:Shri\.\s*)?((?:(?!M\.A\.C\.P\. No\.)[^\d,\n])+).*?Age.*?(\d+).*?Occ\s*:\s*([^\n]+)',re.IGNORECASE | re.DOTALL)
    address_pattern = re.compile(r'R[/@]t?\s*[-–]?\s*([\w\s,.()]+)(?=\.\s*|,)',re.IGNORECASE)

    addresses = address_pattern.findall(first_two_pages_text)
    detailed_applicants = detailed_pattern.findall(cleaned_text)
    simple_applicants = simple_pattern.findall(first_two_pages_text)
    applicants = detailed_applicants[:6] + simple_applicants[:6 - len(detailed_applicants)]
    applicant_data = {}
    for i, details in enumerate(applicants, start=1):
        if len(details) == 6:
            # Unpack 6 values
            num, prefix, name, age, occupation, _ = details
            applicant_data[f'Applicant {i} Number'] = num.strip() if num else " "
            applicant_data[f'Applicant {i} Name'] = f"{prefix.strip()} {name.strip()}" if prefix else name.strip()
            applicant_data[f'Applicant {i} Age'] = age.strip()
            applicant_data[f'Applicant {i} Occupation'] = occupation.strip()

        elif len(details) == 4:
            # Unpack 4 values
            num, name, age, occupation = details
            applicant_data[f'Applicant {i} Number'] = num.strip() if num else " "
            applicant_data[f'Applicant {i} Name'] = name.strip()
            applicant_data[f'Applicant {i} Age'] = age.strip()
            applicant_data[f'Applicant {i} Occupation'] = occupation.strip()

        # Assign address to each applicant
        if i - 1 < len(addresses):
            applicant_data[f'Applicant {i} Address'] = addresses[i - 1].strip()
        else:
            applicant_data[f'Applicant {i} Address'] = ""

    #print(applicant_data)
    return applicant_data


def add_applicant_columns(df, max_applicants):
    for i in range(1, max_applicants + 1):
        df[f'Applicant {i} Number'] = None
        df[f'Applicant {i} Name'] = None
        df[f'Applicant {i} Age'] = None
        df[f'Applicant {i} Occupation'] = None

def extract_opponents(cleaned_text, first_two_pages_text):
    # Existing detailed opponent pattern
    detailed_opponent_pattern = re.compile(r'(\d+)-?\s*(?:(Mr\.|Ms\.|Mrs\.|Smt\.|The Manager,|M/s)\s+)?([A-Za-z\s.]+?),?\s*Age\s*[:-]?\s*(\d+)\s*years?,?\s*Occ\.*\s*[:-]?\s*([A-Za-z\s]+),?\s*R?/?at\s*([A-Za-z0-9,\s.\/-]+)',re.IGNORECASE)
    # Updated general opponent pattern to match the provided samples
    general_opponent_pattern = re.compile(r'(?:Vs\.|V/s)\s+([A-Za-z\s.]+?)(?:\s+&\s+|\s+and\s+|\s*[/]\s*|\s*[\]\[]\s*|$)',re.IGNORECASE   )

    # Extract detailed opponents from the complete text
    detailed_opponents = detailed_opponent_pattern.findall(cleaned_text)
    # Extract general opponents from only the first two pages
    general_opponents = general_opponent_pattern.findall(first_two_pages_text)
    opponent_data = {}
    # Process detailed opponents
    for i, (num, prefix, name, age, occupation, address) in enumerate(detailed_opponents, start=1):
        opponent_data[f'Opponent {i} Number'] = num.strip()
        opponent_data[f'Opponent {i} Name'] = f"{prefix.strip()} {name.strip()}" if prefix else name.strip()
        opponent_data[f'Opponent {i} Age'] = age.strip()
        opponent_data[f'Opponent {i} Occupation'] = occupation.strip()
        opponent_data[f'Opponent {i} Address'] = address.strip()

    # Process general opponents (only from the first two pages)
    for i, opponent in enumerate(general_opponents, start=len(detailed_opponents) + 1):
        opponent = opponent.strip().rstrip(',').strip()
        opponent_data[f'Opponent {i} Name'] = opponent
    return opponent_data


def process_pdfs_in_folder(folder_path, df):
    all_files = os.listdir(folder_path)
    pdf_files = [file for file in all_files if file.lower().endswith('.pdf')]
    for pdf_file in pdf_files:
        pdf_path = os.path.join(folder_path, pdf_file)
        print(f"Processing {pdf_file}...")
        cleaned_text = extract_and_clean_text_from_pdf(pdf_path)
        doc = nlp(cleaned_text)
        doc = fitz.open(pdf_path)
        first_two_pages_text = ""
        for page_num in range(min(2, doc.page_count)):
            first_two_pages_text += doc[page_num].get_text()

        # Define patterns for each date

        received_or_presented_on_pattern = re.compile(r'(?:RECEIVED ON|Presented on)\s*:\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        #received_or_presented_on_pattern = re.compile(r'(?:RECEIVED ON|Received on|Presented on)\s*:\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        received_or_presented_on_pattern1 = re.compile(r'Received\s*on\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        registered_on_pattern = re.compile(r'Registered on\s*:\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        decided_on_pattern = re.compile(r'Decided on\s*:\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        duration_pattern_multiline = re.compile(r'Duration\s*:\s*Ys/\s*Ms/\s*Ds/\s*\n\s*(\d{2})\s+(\d{2})\s+(\d{2})', re.IGNORECASE)
        duration_pattern_singleline = re.compile(r'DURATION\s*:\s*(\d+)(?:Ys|Y)[.\s]*(\d+)(?:Ms|M)[.\s]*(\d+)(?:Ds|D)[.\s]*', re.IGNORECASE)

         # Pattern to match 'DURATION : 3Ys.3Ms.2Ds.' format
        pattern_duration_uppercase = re.compile(r'DURATION\s*:\s*(\d+)(?:Ys|Y)[.\s]*(\d+)(?:Ms|M)[.\s]*(\d+)(?:Ds|D)[.\s]*', re.IGNORECASE)
        pattern_duration_colon = re.compile(r'Duration:\s*(\d+)\s*Ys[.\s]*(\d+)\s*Ms[.\s]*(\d+)\s*Ds', re.IGNORECASE)
        pattern_duration_combined = re.compile(r'(\d+)\s*Ys?[.\s]*(\d+)\s*Ms?[.\s]*(\d+)\s*Ds?|(\d+)\s*[Yy][.\s]*(\d{2})\s*[Mm][.\s]*(\d{2})\s*[Dd]s?', re.IGNORECASE)

        # Flexible pattern to match various formats, including negative values for months
        pattern_duration_flexible = re.compile(r'DURATION\s*:\s*(-?\d+)\s*(?:Ys?\.?|Y\.?)\s*(-?\d*)\s*(?:Ms?\.?|M\.?)\s*(-?\d*)\s*(?:Ds?\.?|D\.?)', re.IGNORECASE)

        # Regular expression to extract years, months, and days

        pattern_duration_flexible2 = re.compile(r'--Y\.(\d+)Ms\.(\d+)Ds\.')
        pattern_duration_flexible1 = re.compile(r'Duration\s*Ys\.\s*Ms\.\s*Ds\.\s*(\d+)\s*(\d*)\s*(\d*)', re.IGNORECASE )

        #pattern_duration_colon1 = re.compile(r'Duration: :\s*(\d+)\s*Y[.\s]*(\d{2})\s*M[.\s]*(\d{2})\s*Ds', re.IGNORECASE)

        # Search for each date

        received_on_match = received_or_presented_on_pattern.search(cleaned_text)
        received_on_match1 = received_or_presented_on_pattern1.search(cleaned_text)
        registered_on_match = registered_on_pattern.search(cleaned_text)
        decided_on_match = decided_on_pattern.search(cleaned_text)
        # Extract dates
        received_on = received_on_match.group(1) if received_on_match else received_on_match1.group(1) if received_on_match1 else " "
        registered_on = registered_on_match.group(1) if registered_on_match else " "
        decided_on = decided_on_match.group(1) if decided_on_match else " "
 
        def extract_durations(cleaned_text):
            # Check if the word "Duration:" is present in the input text
            if "Duration :" in cleaned_text:
                # Extract all numbers following "Duration:" from the input text
                numbers = [int(match) for match in re.findall(r'\b(\d+)\b', cleaned_text.split("Duration :")[1])]
                # Initialize years, months, and days
                years = numbers[0] if len(numbers) > 0 else 0
                months = numbers[1] if len(numbers) > 1 else 0
                days = numbers[2] if len(numbers) > 2 else 0
                duration = f"{years} years, {months} months, {days} days"
                return duration

            else:

                return " "


        # Extract durations

        duration_match_multiline = duration_pattern_multiline.search(cleaned_text)
        duration_match_singleline = duration_pattern_singleline.search(cleaned_text)
        match_duration_uppercase = pattern_duration_uppercase.search(cleaned_text)
        pattern_duration_colon = pattern_duration_colon.search(cleaned_text)
        match_duration_combined = pattern_duration_combined.search(cleaned_text)

        # Extract durations based on the flexible pattern
        match_duration_flexible = pattern_duration_flexible.search(cleaned_text)
        # Extract durations based on the flexible pattern
        match_duration_flexible1 = pattern_duration_flexible1.search(cleaned_text)
        # Search for the pattern in the line
        match_duration_flexible2 = pattern_duration_flexible2.search(cleaned_text)
        if duration_match_multiline:
            years, months, days = duration_match_multiline.groups()
            duration = f"{years} years, {months} months, {days} days"
        elif duration_match_singleline:
            years, months, days = duration_match_singleline.groups()
            duration = f"{years} years, {months} months, {days} days"

        elif match_duration_uppercase:
            years, months, days = match_duration_uppercase.groups()
            duration = f"{years} years, {months} months, {days} days"

        elif pattern_duration_colon:
            years, months, days = pattern_duration_colon.groups()
            duration = f"{years} years, {months} months, {days} days"
        elif match_duration_combined:
            groups = [group for group in match_duration_combined.groups() if group is not None]
            years, months, days = map(int, groups)
            duration = f"{years} years, {months} months, {days} days"

        elif match_duration_flexible:
            years, months, days = match_duration_flexible.groups()
            # Handle cases where years or days might be empty
            years = 0 if not years or years == '-' or years == '--' else int(years)
            months = 0 if not months or months == '-' else int(months)
            days = 0 if not days or  days == '-' else int(days)
            duration = f"{years} years, {months} months, {days} days"

        elif match_duration_flexible1:
            years, months, days = match_duration_flexible1.groups() 
            # Handle cases where years or days might be empty
            years = 0 if not years else int(years)
            months = 0 if not months else int(months)
            days = 0 if not days else int(days)
            duration = f"{years} years, {months} months, {days} days"
            # Check if a match is found and extract values

        elif match_duration_flexible2:
            months = int(match_duration_flexible2.group(1))
            days = int(match_duration_flexible2.group(2))
            years = 0
            duration = f"{years} years, {months} months, {days} days" 
        else:
            duration = extract_durations(cleaned_text)
            #print(duration)

        # Case Number
        case_number_pattern = re.compile(

            r'M\.?A\.?C\.?P\.?\s*No\.?\s*(\d+)(?:\/(\d+))?',

            re.IGNORECASE

        )

        case_number_match = case_number_pattern.search(cleaned_text)

        if case_number_match:

            # Construct the case number from the matched groups

            case_number = "MACP No." + case_number_match.group(1)

            if case_number_match.group(2):

                case_number += "/" + case_number_match.group(2)

        else:

            case_number = ""

        # CNR Number

        cnr_number_pattern = re.compile(

            r'(?:CNR No\.?|CNR)\s*:? MHPU\d{2}-?\s*0?\d{3,6}-\d{4}|MHPU\d{2}\D*\d{6}\D*\d{4}|MHPU\d{2}-?\d{3,6}-\d{4}',

            re.IGNORECASE
 
        )

        cnr_number_match = cnr_number_pattern.search(cleaned_text)
        if cnr_number_match:
            cnr_number = cnr_number_match.group(0).replace("CNR No. ", "").replace("CNR No", "").replace("CNR ", "").replace("\n", "").replace(" ", "")
        else:
            cnr_number = ""

        #Court Title
        court_title_pattern = re.compile(

            r'BEFORE THE (NATIONAL LOK-ADALAT, HELD AT PUNE|MEMBER, MOTOR ACCIDENT CLAIMS\s+TRIBUNAL, PUNE AT PUNE)',

            re.IGNORECASE | re.DOTALL

        )

        court_title_match = court_title_pattern.search(cleaned_text)

        if court_title_match:

            court_title = court_title_match.group(0).strip()

        else:

            court_title = ""


        # Judge Name

        judge_name_pattern = re.compile(r'Digitally signed by (.+?) Date:')

        judge_name_match = judge_name_pattern.search(cleaned_text)

        judge_name = judge_name_match.group(1).strip() if judge_name_match else ""

        old_claim_pattern = re.compile(r'Claim Application under Section\s+(\d+)\s+of the Motor Vehicles Act')

        old_claim_match = old_claim_pattern.search(cleaned_text)

        # New Claim Under Section pattern (for Legal Services Authority Act, 1987)

        new_claim_pattern = re.compile(r'Pune under Section (\d+) of the Legal Services Authority Act, 1987')

        new_claim_match = new_claim_pattern.search(cleaned_text)

        # Determine which pattern matches and use that

        if old_claim_match:

            claim_info = f"Section {old_claim_match.group(1)} of the Motor Vehicles Act"

        elif new_claim_match:

            claim_info = f"Section {new_claim_match.group(1)} of the Legal Services Authority Act, 1987"

        else:

            claim_info = ""

        # Brief Description of the Accident

        accident_description_pattern = re.compile(r'The petition in short, is as under\s*:\s*(.*?)(?=\. On)', re.DOTALL)

        accident_description_match = accident_description_pattern.search(cleaned_text)

        accident_description = accident_description_match.group(1).strip() if accident_description_match else ""

        # Date of Accident

        date_pattern = re.compile(r'which took place on (\d{2}\.\d{2}\.\d{4})')

        date_match = date_pattern.search(cleaned_text)

        accident_date = date_match.group(1).strip() if date_match else ""

        # Place of Accident

        place_pattern = re.compile(r'on\s([^\,\.]+? road in [^\,\.]+)(?:\.|\,)|in front of ([^\,\.]+), near [^\,\.]+, ([^\,\.]+)', re.IGNORECASE)
        place_match = place_pattern.search(cleaned_text)
        if place_match:
            if place_match.group(1):
                accident_place = place_match.group(1).strip()
            else:
                accident_place = place_match.group(2).strip() + ", " + place_match.group(3).strip()
        else:
            accident_place = ""

        # Death/Injury Details
        death_injury_pattern = re.compile(r'(deceased was seriously injured and succumbed to injuries|account of accidental death of [\w\s]+)', re.IGNORECASE)
        death_injury_match = death_injury_pattern.search(cleaned_text)
        death_injury_details = death_injury_match.group(0) if death_injury_match else ""

        # Registration No of vehicle 1
        registration_pattern = re.compile(r'registration No\.?\s*([A-Z]{2}-?\s?[0-9]{2}-?\s?[A-Z]*-?\s?[0-9]{4})',re.IGNORECASE)
        registration_match = registration_pattern.search(cleaned_text)
        registration_number = registration_match.group(1).strip() if registration_match else ""

        # Deceased/Victim Name
        name_pattern = re.compile(r'Deceased\s+([A-Za-z]+(?:\s+[A-Za-z]+){0,2})', re.IGNORECASE)
        deceased_names = name_pattern.findall(cleaned_text)
        if deceased_names:
            cleaned_deceased_name = deceased_names[0].strip()
        else:
            cleaned_deceased_name = ""

        # Deceased/Victim Age
        age_pattern = re.compile(r'age(?:d)?\s+(\d+)(?:\s+years(?:\s+old)?)?', re.IGNORECASE)
        age_match = age_pattern.search(cleaned_text)
        deceased_victim_age = age_match.group(1) if age_match else ""

        # Deceased/Victim Income
        income_pattern = re.compile(r'(?:earning|salary)\s+Rs\.\s*([0-9,/-]+)(?:\s+per month|\s+monthly)?', re.IGNORECASE)
        income_match = income_pattern.search(cleaned_text)
        deceased_victim_income = income_match.group(1) if income_match else ""

        # Deceased/Victim's Occupation
        occupation_pattern = re.compile(r'worked in ([\w\s]+) as ([\w\s]+)')
        occupation_match = occupation_pattern.search(cleaned_text)
        if occupation_match:
            company = occupation_match.group(1).strip()
            position = occupation_match.group(2).strip()
            deceased_victim_occupation = f"{position} at {company}"
        else:
            deceased_victim_occupation = ""

        # Account Number
        account_number_pattern = re.compile(r'Account Number\s*[-:]*\s*(\d+)', re.IGNORECASE)
        account_number_match = account_number_pattern.search(cleaned_text)
        account_number = account_number_match.group(1).strip() if account_number_match else ""
        #print(account_number)
        account_name_pattern = re.compile(r'Account Name\s*[-:]\s*([-\w\s,]+)',re.IGNORECASE)
        account_name_match = account_name_pattern.search(cleaned_text)
        account_name = account_name_match.group(1).strip() if account_name_match else ""
        #print(account_name)

        # Bank Name
        bank_name_pattern = re.compile(r'(State Bank of India),\s*(\w+)\s+Court Branch,\s*(Pune)|Name of Bank\s*[-:]\s*(.*?),\s*(.*?)\s+Court Branch,\s*(\w+)', re.IGNORECASE)
        bank_name_match = bank_name_pattern.search(cleaned_text)

        if bank_name_match:
            # Check if the first group (State Bank of India) is not None
            if bank_name_match.group(1) is not None:
                bank_name = bank_name_match.group(1).strip()
            # Check if the fifth group (Name of Bank) is not None
            elif bank_name_match.group(5) is not None:
                bank_name = bank_name_match.group(5).strip()
            else:
                bank_name = ""
        else:
            bank_name = ""

        # IFSC Code
        ifsc_code_pattern = re.compile(r'IFSC Code\s*[-:]*\s*(SBIN\d{6})',re.IGNORECASE)
        ifsc_code_match = ifsc_code_pattern.search(cleaned_text)
        ifsc_code = ifsc_code_match.group(1).strip() if ifsc_code_match else ""

        # Claim Rs.
        claim_pattern = re.compile(r'Claim Rs\.\s*([\d,/-]+)')
        claim_match = claim_pattern.search(cleaned_text)
        claim_amount = claim_match.group(1).strip() if claim_match else ""

        # Advocate for Applicants
        advocate_pattern = re.compile(r'Advocate for Applicants\s*:\s*([\w\s.]+?)(?=,\s*Shri\.|For opponent|$)',re.IGNORECASE | re.DOTALL)
        advocate_match = advocate_pattern.search(cleaned_text)
        advocate_name = advocate_match.group(1).strip() if advocate_match else ""

        # Advocate for opponent No.1
        advocate_opponent1_pattern = re.compile(r'Advocate for opponent No\.1\s*:\s*(.*?)(?=\s*Advocate for opponent No\. 2)', re.IGNORECASE | re.DOTALL)
        advocate_opponent1_match = advocate_opponent1_pattern.search(cleaned_text)
        advocate_opponent1_name = advocate_opponent1_match.group(1).strip() if advocate_opponent1_match else ""

        # Advocate for opponent No.2
        advocate_opponent2_pattern = re.compile(r'Advocate for opponent No\. 2\s*:\s*((?:Shri\.?\s+[A-Z]\.\s+[A-Z]\.\s+\w+)(?:\s*,\s*(?:Shri\.?\s+[A-Z]\.\s+[A-Z]\.\s+\w+))*)', re.IGNORECASE | re.DOTALL)
        advocate_opponent2_match = advocate_opponent2_pattern.search(cleaned_text)
        advocate_opponent2_name = advocate_opponent2_match.group(1).strip() if advocate_opponent2_match else ""

        # Name of Steno
        steno_pattern = re.compile(r'Name of Steno : (.+?) Date of order')
        steno_match = steno_pattern.search(cleaned_text)
        steno_name = steno_match.group(1).strip() if steno_match else ""

        # Order uploaded on
        order_uploaded_pattern = re.compile(r'Order uploaded on : (\d{2}\.\d{2}\.\d{4})')
        order_uploaded_match = order_uploaded_pattern.search(cleaned_text)
        order_uploaded_date = order_uploaded_match.group(1).strip() if order_uploaded_match else ""

        # Date of Order
        date_of_order_pattern = re.compile(r'Date of order : (\d{2}\.\d{2}\.\d{4})')
        date_of_order_match = date_of_order_pattern.search(cleaned_text)
        date_of_order = date_of_order_match.group(1).strip() if date_of_order_match else ""
        
        insurance_company_pattern = re.compile(r'\b(?:[A-Za-z]+\s)*(?:Insurance|Insurer|Ltd\.|Limited|Corporation|Corp\.|Company|Co\.|Group)\b',re.IGNORECASE)
        insurance_company_match = insurance_company_pattern.search(cleaned_text)
        insurance_company_name = insurance_company_match.group(0).strip() if insurance_company_match else " "
        
        medical_expenses_pattern = re.compile(r'Medical expenses Rs\.\s*([\d,/-]+)',re.IGNORECASE)
        medical_expenses_match = medical_expenses_pattern.search(cleaned_text)
        medical_expenses = medical_expenses_match.group(1).strip() if medical_expenses_match else " "

        fir_number_pattern = re.compile(r'FIR Exh\.\s*(\d+)',re.IGNORECASE)
        fir_number_match = fir_number_pattern.search(cleaned_text)
        fir_number = fir_number_match.group(1).strip() if fir_number_match else " "

        police_station_pattern = re.compile(r'Police Station,\s*([A-Za-z ]+)',re.IGNORECASE)
        police_station_match = police_station_pattern.search(cleaned_text)
        police_station_name = police_station_match.group(1).strip() if police_station_match else " "

        hospital_pattern = re.compile(r'(?:First hospital details\s+)?([A-Za-z ]+ Hospital)\s*(?:,|\b)(?:\s*Second hospital details\s+([A-Za-z ]+ Hospital))?',re.IGNORECASE)
        hospital_match = hospital_pattern.search(cleaned_text)
        first_hospital = hospital_match.group(1).strip() if hospital_match and hospital_match.group(1) else " "
        second_hospital = hospital_match.group(2).strip() if hospital_match and hospital_match.group(2) else None
        
        applicant_data = extract_applicants(cleaned_text, first_two_pages_text)
        opponent_data = extract_opponents(cleaned_text, first_two_pages_text)


        written_statement_pattern = re.compile(r'(Exh\.\s*\d+\s+(?:opponent\s*No\.?1|respondent)\s+filed\s+written\s+statement)(.*?)(?=Exh\.|\Z)',re.IGNORECASE)
        written_statement_match = written_statement_pattern.findall(cleaned_text)
        written_statement_content = " ".join([match[1].strip() for match in written_statement_match])
        
        written_statement_opponent2_pattern = re.compile(r'(Exh\.\s*\d+\s+opponent\s*No\.?2\s+filed\s+written\s+statement)(.*?)(?=Exh\.|\Z)',re.IGNORECASE | re.DOTALL)
        written_statement_opponent2_matches = written_statement_opponent2_pattern.findall(cleaned_text)
        written_statement_opponent2_content = " ".join([match[1].strip() for match in written_statement_opponent2_matches])

        judgment_date_pattern = re.compile(r'Delivered on (?:this )?(\d{1,2})(?:st|nd|rd|th)?\s+Day of (\w+)\s+(\d{4})', re.IGNORECASE)
        judgment_date_match = judgment_date_pattern.search(cleaned_text)
        if judgment_date_match:
            day, month, year = judgment_date_match.groups()
            judgment_date = f"{day} {month} {year}"
        else:
            judgment_date = ""


        marital_status_pattern = re.compile(r'Deceased\s+(?:was\s+)?(married|bachelor)', re.IGNORECASE)
        marital_status_match = marital_status_pattern.search(cleaned_text)
        if marital_status_match:
            marital_status = marital_status_match.group(1)
        else:
            marital_status = " "

        witness_no_1_pattern = re.compile(r'([A-Za-z\s.]+)\s+is\s+examined\s+as\s+witness\s+No\.?\s*1', re.IGNORECASE)
        # Search for witness No. 1 in the text
        witness_no_1_match = witness_no_1_pattern.search(cleaned_text)

        # Extract the witness number
        witness_no_1 = witness_no_1_match.group() if witness_no_1_match else ""  
        witness_no_2_pattern = re.compile(r'([A-Za-z\s.]+)\s+as\s+witness\s+No\.?\s*2', re.IGNORECASE)

        # Search for witness No. 2 in the text
        witness_no_2_match = witness_no_2_pattern.search(cleaned_text)

        # Extract the witness number
        witness_no_2 = witness_no_2_match.group() if witness_no_2_match else ""
        
        future_prospect_pattern = re.compile(r'Add[-:]?\s*(\d+)%\s*future\s*prospects?', re.IGNORECASE)

        # Search for the future prospect pattern in the text
        future_prospect_match = future_prospect_pattern.search(cleaned_text)

        # Extract the future prospect value if a match is found, otherwise set it to an empty string
        future_prospect_value = future_prospect_match.group(1).strip() if future_prospect_match else " "
        
        # Define the multiplier pattern
        multiplier_pattern = re.compile(r'Multiplier\s+(\d+)', re.IGNORECASE)

        # Search for the multiplier pattern in the text
        multiplier_matches = multiplier_pattern.findall(cleaned_text)

        # Extract the first multiplier value if matches are found, otherwise set it to an empty string
        multiplier_value = multiplier_matches[0].strip() if multiplier_matches else ""
        
        
        # Define the pattern
        custom_pattern = re.compile(r'Loss of spousal and filial consortium & Funeral Expenses & Loss of Estate Rs\.([\d,/-]+) \((.*)\)')

        # Search for the pattern in the text
        custom_matches = custom_pattern.findall(cleaned_text)

        # Extract the matched values
        custom_value = custom_matches[0][0].strip() if custom_matches else ""
        
        
        notional_income_pattern = re.compile(r'notional\s*income.*?Rs\.([\d,/-]+)', re.IGNORECASE)

        # Search for the notional income pattern in the text
        notional_income_matches = notional_income_pattern.findall(cleaned_text)

        # Extract the notional income values if matches are found, otherwise set it to an empty list
        notional_income_values = [match.strip() for match in notional_income_matches] if notional_income_matches else " "


        # Interest Rate
        interest_rate = ""
        phrases_to_check = ['interest on the total compensation', 'interest', 'amount at the rate of']
        for phrase in phrases_to_check:
            if phrase in cleaned_text:
                received_on_index = cleaned_text.find(phrase)
                if received_on_index != -1:
                    received_on_content = cleaned_text[received_on_index + len(phrase):].strip()
                    interest_rate_match = re.search(r'@ (\d+(\.\d+)?)% per annum', received_on_content)
                    if interest_rate_match:
                        interest_rate = interest_rate_match.group(1)
                        break  # Break the loop once interest rate is found

        # Create a dictionary to hold the extracted information
        info_dict = {col: "" for col in all_columns}
        info_dict = {
            "File Name": pdf_file,
            "RECEIVED ON": received_on,
            "REGISTERED ON": registered_on,
            "DECIDED ON": decided_on,
            "DURATION": duration,
            "Case Number": case_number,
            "CNR Number": cnr_number,
            "Court Title": court_title,
            "Judge Name": judge_name,
            "Claim Under Section": claim_info,
            "Brief Description of the Accident": accident_description,
            "Date of Accident": accident_date,
            "Place of Accident": accident_place,
            "Death/Injury Details": death_injury_details,
            "Registration No of vehicle 1": registration_number,
            "Deceased/Victim Name": cleaned_deceased_name,
            "Deceased/Victim Age": deceased_victim_age,
            "Deceased/Victim Income": deceased_victim_income,
            "Deceased/Victim's Occupation": deceased_victim_occupation,
            "Account Number": account_number,
            "Account_Name" : account_name,

            #"Bank Name": bank_name,

            "IFSC Code": ifsc_code,
            "Claim Rs.": claim_amount,
            "Advocate for Applicants": advocate_name,
            "Advocate for opponent No.1": advocate_opponent1_name,
            "Advocate for opponent No.2": advocate_opponent2_name,
            "Name of Steno": steno_name,
            "Order uploaded on": order_uploaded_date,
            "Date of Order": date_of_order,
            "Insurance company name":insurance_company_name,
            "Medical expenses":medical_expenses,
            "Fir number":fir_number,
            "Police station name":police_station_name,
            "First hospital name":first_hospital,
            "Second hospital name":second_hospital,
            "Written Statement by Opponent No.1":written_statement_content,
            "Written Statement by Opponent No.2":written_statement_opponent2_content,
            "Judgment Date" : judgment_date,
            "Deceased Marital Status" : marital_status,
            "Witness No 1 " : witness_no_1,
            "Witness No 2 "  : witness_no_2,
            "Future Prospect": future_prospect_value,
            "Multiplier": multiplier_value,
            "Loss of spousal and filial consortium & Funeral Expenses & Loss of Estate": custom_value,
            "Notional Income": notional_income_values,
            "Interest Rate": interest_rate
        }

        info_dict.update(applicant_data)
        info_dict.update(opponent_data)
        #print(f"eachfile{info_dict}")

        # Append the information to a list of DataFrames
        dfs = [df, pd.DataFrame([info_dict])]
        df = pd.concat(dfs, ignore_index=True)
        #print(df)
    return df

def unique_file_with_timestamp(base_path, suffix='.xlsx'):
    """Generate a unique file path with a timestamp, appending numbers if necessary."""

    timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")
    counter = 1
    new_path = f"{base_path}_{timestamp}{suffix}"
    while os.path.exists(new_path):
        new_path = f"{base_path}_{timestamp}_{counter}{suffix}"
        counter += 1
    return new_path
 
 


# Example usage
folder_path = r"D:\Bajaj\All"  # Replace with your folder path
df = pd.DataFrame(columns=all_columns)
result_df = process_pdfs_in_folder(folder_path, df)
 
 
# Find a unique filename with timestamp and save the DataFrame
base_filename = "Downloads"  # Base path for the file
unique_filename = unique_file_with_timestamp(base_filename)
result_df.to_excel(unique_filename, index=False)

 
# Print success message
print(f"File exported successfully as '{unique_filename}'")

Processing 465 2022.pdf...

Processing MACP  34 2021.pdf...

Processing MACP 1 2020.pdf...
Presented on : 07/01/2020 Registered on : 07/01/2020 Decided on : 01/12/2022 Duration : Ys/ Ms/ Ds/ 02 11 23 BEFORE THE MEMBER, MOTOR ACCIDENT CLAIMTRIBUNAL, PUNE AT ­ PUNE. ( Presided over by Shri. S.B. Hedaoo) Motor Accident Claim Petition No. 01/2020 CNR NO : MHPU01­000424­2020 Exh. No. 1] Smt. Vanita Balbhim Rupnur Age : 20 years, Occ. Household, R/at – Wadki, Tal Haveli, Dist Pune. 2] Mrs. Sundrabai Shrimant Karnure Age : 55 years, Occu : Household, 3] Mr. Shirmant Nagnath Karnure Age : 60 yrs., Occu – Nil, R/at : Nai Chakur, Umarga, Osmanabad. ….Applicant Vs. 1] Mr. Rama Babu Kudaskar Age : 56 yrs., Occu : Business, R/at : H.No. 32, Wathadev Karapur, Bicholim, Sankhalim, North Goa – 403 506. 2] The Manager, Bajaj Allianz General Insurance Co. Ltd., Off – 'Vardhman', 7 Loves Chowk, Shankarsheth Road, Pune – 411 042. ....Opponent Claim of Rs. 35,00,000/­ MACP No. 01/2020 2 CNR No. MHPU01­0004

Processing MACP 1 2021.pdf...
CNR No. 1 M.A.C.P. No.1/2021 MHPU01-014037-2020 Judgment RECEIVED ON : 20.12.2020 REGISTERED ON : 05.01.2021 DECIDED ON : 24.04.2023 DURATION : 2Ys.3Ms.20Ds. BEFORE THE MEMBER, MOTOR ACCIDENT CLAIMS TRIBUNAL, PUNE AT PUNE (Presided over by B. P. Kshirsagar) MACP No.1/2021 EXH No. 43 1- Smt. Chhaya Ganesh Kasbe Age 35 years old, Occ : Household 2- Hrishikesh Ganesh Kasbe Age 14 years old, Occ : Student 3- Arushi Ganesh Kasbe Age 12 years old, Occ : Student (Applicant Nos. 2 and 3 are minor hence claiming through applicant No. 1 their mother) 4- Bhimrao Pandhari Kasbe Age 65 years old, Occ : labour All R/o Laxminagar, Yerwada, Pune. ....Applicants Versus 1- Kamannand Mahalappa Hekade Age major , occ : Transport (Registered owner of Truck A/P Ratnagiri Housing Society, RH08, B-10 G Block, near Sai Garden, MIDC Pune 411019. CNR No. 2 M.A.C.P. No.1/2021 MHPU01-014037-2020 Judgment 2- Divisional Manager. ICICI Lombard General Insurance Company Limited. Office No

Processing MACP 10 2022.pdf...
1 MACP No. 10/2022 CNR-MHPU01-020244-2021 M.A.C.P No.10/2022 Jyoti Thopte+4 Vs. Sunil+1 Order below Claim Petition vide Exh.1 (Passed on this 28 th day of July, 2023) 1. Matter was referred to the mediation. Mediation report is at Exh.15 in respect of settlement of claim in between the parties. Joint compromise memo is at Exh.16 in respect of full & final settlement of claim between the parties for Rs.13,50,000/- inclusive of N. F. L. amount, interest, medical & hospital bills and costs. Learned Advocate for respondent No.2 has filed the xerox copy of settlement letter issued by the opponent No.2 in his favour at Exh.17. 2. As the matter has been settled between the applicants and opponent No.2 as per the joint compromise memo vide Exh.16, the instant claim petition is liable to be disposed-of in terms of joint compromise memo accordingly, and I proceed to pass following order. O R D E R 1. Claim petition is disposed-of in terms of joint compromise memo v

Processing MACP 102 2020.pdf...

Processing MACP 102 2021.pdf...

Processing MACP 103 2022.pdf...

Processing MACP 105 2022.pdf...

Processing MACP 106 2020.pdf...
CNR No. MACP No. 106/2020 MHPU01-004408-2020 Pravin Murlidhar Dawkhare V/s Sandip Lalasaheb Jadhav ors. ORDER BELOW EXH.1 (Dated 26 th day of July 2022) 1- In view of Mediator Report (Exh.20) and compromise pursis (Exh.19) the matter is amicably settled between applicant and Opponent No.3 for an amount of Rs.8,00,000/- (inclusive of NFL amount) 2- As such claim is disposed off as compromised. 4- Opponent Nos. 1 and 2 are discharged from any liability. 5- Amount of compensation of Rs.8,00,000/- be paid to applicant after it is deposited by opponent No. 3, by account payee cheque, on due verification. 6- Award be drawn up accordingly. 7- Amount of court Fee be refunded as per rule. (B.P. Kshirsagar) Member, Pune Motor Accident Claims Tribunal, Date : 26.07.2022 Pune. Digitally signed by BHUSHAN PRAKASH KSHIRSAGAR Date: 2022.07

Processing MACP 110 2022.pdf...
CNR No. 1 MACP No.110/2022 MHPU01-005043-2022 BEFORE THE NATIONAL LOK-ADALAT, HELD AT PUNE [ Organized by District Legal Services Authority, Pune under Section 19 of the Legal Services Authority Act, 1987 ] Aditya Dilip Raje V/s The New India Assurance Co. Ltd. & others. ORDER CUM AWARD The matter has been placed before National Lok- Adalat held on 09.09.2023. The parties have amicably settled the matter in the National Lok-Adalat before the Panel consisting of (1)Shri. B. P. Kshirsagar, Member, MACT, Pune & Head of Panel and (2) Adv. Shri.A.B.Gunjal Member of Panel for Rs.1,50,000/- including NFL amount in terms of compromise pursis Exh.19. In view of amicable settlement, following Award is passed. 1- The Opponent No.3 The New India Assurance Co. Ltd. do pay total compensation of Rs. 1,50,000/- ( Rs. One Lakhs Fifty Thousand only) to the petitioner within a period of one month from the date of this order. On failure, the petitioner are entitled to recei

...

Processing MACP 74 2020.pdf...

Processing MACP 74 2021.pdf...

Processing MACP 76 2021.pdf...
1 MACP No.76/2021 Smt. Nanda Lokhande V/s. Gurumal Singh Uppal MHPU01002559-2021 ORDER BELOW (EXH.1 ) IN MOTOR ACCIDENT CLAIM PETITION NO.76/20121 Applicant Nanda Bhausaheb Lokhande and her Advocate are present. The Advocate for respondent No.2 Bajaj Allianz General Insurance Co. Ltd is present. The authority letter is also filed at Exh. 24. 2. Perused the mediation report Exh.25. The applicant and opponent No.2 have filed a joint compromise purshis Exh.23 mentioning that the dispute is settled for a lump sum amount of Rs.3,00,000/­ inclusive of NFL amount and all other amounts recoverable from opponent No.2. They have requested to dispose of the petition in terms of pursis Exh.23. 3. The contents of purshis Exh.23 are explained to the applicant. She admits it's content. Hence, the order ORDER 1] The petition is allowed in terms of pursis Exh.23. 2] Opponent No.2 shall deposit an amount of Rs

Processing MACP 81 2022.pdf...

Processing MACP 82 2021.pdf...

Processing MACP 83 2023.pdf...
CNR No.MHPU21-003384-2023 1 MACP No.83/2023 BEFORE THE NATIONAL LOK-ADALAT, HELD AT PUNE [ Organized by District Legal Services Authority, Pune under Section 19 of the Legal Services Authority Act, 1987 ] Mr. Laxman Hariba Jadhav ….Applicant. Vs. Shri. Sankesh Dilip Surana and others ….Opponents. ORDER CUM AWARD The matter has been placed before National Lok- Adalat held on 09/12/2023. The parties have amicably settled the matter in the National Lok-Adalat before the Panel consisting of (1) Shri. S. S. Gulhane, Member, MACT, Pune & Head of Panel and (2) Adv. Smt. Jayshri Wackchaure Member of Panel for Rs.7,25,000/- (Rs. Seven Lakhs Twenty Five Thousand only) including NFL amount in terms of compromise pursis Exh.18, which is already paid. In view of amicable settlement, following Award is passed. 1- The Opponent No.2 Reliance General Insurance Ltd., do pay total compensation of Rs.7,00,000/- 

Processing MACP 92 2021.pdf...
CNR No. 1 MACP No. 92/2021 MHPU01­003205­2021 BEFORE THE NATIONAL LOK­ADALAT, HELD AT PUNE [ Organized by District Legal Services Authority, Pune under Section 19 of the Legal Services Authority Act, 1987 ] Mira Baban Kate and Ors. V/s Bajaj Allianz Gen. Ins. Co. Ltd. & Ors. ORDER CUM AWARD The matter has been placed before National Lok­ Adalat held on 11.02.2023. The parties have amicably settled the matter in the National Lok­Adalat before the Panel consisting of (1) Shri. B. P. Kshirsagar, Member, MACT, Pune & Head of Panel, (2) Adv. Shri. A.B.Gunjal, Members of Panel for Rs. 17,50,000/­ including NFL amount in terms of compromise pursis Exh. 13. In view of amicable settlement, following Award is passed. 1­ The Opponent No.3 Bajaj Allianz General Insurance Co. Ltd. do pay total compensation of Rs. 17,50,000/­ ( Rs. Seventeen Lakhs Fifty Thousand only) to the petitioners within a period of one month from the date of this order. On failure, the petitione


Processing MACP 97 2021.pdf...

Processing MACP 98 2022.pdf...

Processing MACP 98 2023.pdf...

Processing MACP 99 2020.pdf...
Presented on : 03/02/2020 Registered on : 04/03/2020 Decided on : 21/09/2023 Duration : Ys/ Ms/ Ds/ 03 06 18 BEFORE THE MEMBER, MOTOR ACCIDENT CLAIM TRIBUNAL, PUNE AT ­ PUNE. ( Presided over by Shri. S.B. Hedaoo) Motor Accident Claim Petition No. 99/2020 CNR NO : MHPU01­004268­2020 Exh. No. 32 Mr. Monish Vishwanath Bhatia, Age – 53 years, Occu. ­ Writer, R/at­ L­602, Celestial City Phase I, Ravet, Pune­ 412 101. …. Applicant Vs. 1] Shri. Rahul Umaji Maske, Age – Adult, Occupation – Business, R/at­A. P. Bhose, Behind Gram Panvhyat Karyalaya, Tal. Khed, Dist. Pune – 410 501. 2] Bajaj Allianz General Insurance Company Ltd. GE Plazna, Airport Road, Yervada, Pune 411 006. ­­ Opponents Claim of Rs. 4,00,000/­ Appearances :­ Adv. Shri. K. S. Khajgiwale for the applicant Opponent No.1 : Exparte. Adv. Shri. Kale for opponent No. 2. MACP No. 99/2020 2 CNR No. MHPU01­004

Processing MACP 99 2022.pdf...
CNR –MHPU01­004147­2022 MACP 99/2022 Rajendra Shelke V/s. Pankaj Meghani ORDER BELOW (EXH.1) IN MACP NO.99/2022 In view of successful mediation as per the report of Hon'ble Mediator Judge dtd.07/10/2022 vide Exh.18, the petition is disposed off as amicably settled. 2] Award be drawn in view of joint compromise memo Exh.16. 3] Deficit court fees, if any, be paid. Date : 07/10/2022 (J. G. Dorle) Additional Member, Motor Accident Claims Tribunal, Pune. CNR –MHPU01­004147­2022 MACP 99/2022 Rajendra Shelke V/s. Pankaj Meghani CERTIFICATE I affirm that the contents of PDF file Judgment are same word for word as per original Judgment. Name of Steno : Pramod S. More (Stenographer G­3) On deputation. Court name : Shri. J. G. Dorle Additional Member, MACT, Pune. Judgment/Order delivered on : 07/10/2022 Judgment/Order signed by P. O. : 18/10/2022 Judgment/Order uploaded on : 21/10/2022
File exported successfully as 'Downloads_20240223_135443.xlsx'


In [1]:
import os
import fitz  # PyMuPDF
import re
import pandas as pd
import spacy

# Load SpaCy model
nlp = spacy.load("en_core_web_sm")
import os
from datetime import datetime

# Define an empty DataFrame with the desired column names
initial_columns  = ["File Name", "RECEIVED ON", "REGISTERED ON", "DECIDED ON", "DURATION", "Case Number", "CNR Number",
            "Court Title", "Judge Name", "Claim Under Section", "Brief Description of the Accident",
           "Date of Accident", "Place of Accident", "Death/Injury Details", "Registration No of vehicle 1",
           "Deceased/Victim Name", "Deceased/Victim Age", "Deceased/Victim Income", "Deceased/Victim's Occupation",
           "Account Number", "Bank Name", "IFSC Code", "Claim Rs.", "Advocate for Applicants",
           "Advocate for opponent No.1", "Advocate for opponent No.2", "Name of Steno", "Order uploaded on",
           "Date of Order","Insurance company name","Medical expenses","Police station name","First hospital name",
           "Second hospital name","Interest Rate"]

# Assuming the maximum number of individual and organization opponents

max_opponents_individual = 5
max_opponents_organization = 5

# Define opponent individual columns

opponent_individual_columns = []
for i in range(1, max_opponents_individual + 1):
    opponent_individual_columns.extend([
        f"Opponent {i} Number", f"Opponent {i} Name", f"Opponent {i} Age",
        f"Opponent {i} Occupation", f"Opponent {i} Address"])

# Define opponent organization columns
opponent_organization_columns = []
for i in range(1, max_opponents_organization + 1):
    opponent_organization_columns.extend([
        f"Opponent Org {i} Number", f"Opponent Org {i} Name", f"Opponent Org {i} Address"])

# Combine all columns
all_columns = initial_columns + opponent_individual_columns
df = pd.DataFrame(columns=all_columns)
def extract_and_clean_text_from_pdf(pdf_path):
    # Open the PDF file
    doc = fitz.open(pdf_path)
    text = ""
    for page in doc:
        text += page.get_text()
    doc.close()

    # Clean the extracted text
    cleaned_text = re.sub(r'\s+', ' ', text)  # Remove unwanted spaces
    cleaned_text = cleaned_text.strip()  # Remove leading and trailing spaces
    print(cleaned_text)
    return cleaned_text

def extract_applicants(cleaned_text, first_two_pages_text):
    # Updated regular expression patterns
    detailed_pattern= re.compile(r'(\d+)-\s*(Mrs\.|Mr\.|Smt\.|Miss)?\s*([\w\s.]+?)\s+Age\s+(\d+)\s+years,\s+Occ\s*:\s*([^\n,]+)(?:,\s+)?(?:Both\s+R\/?at\s+|R\/?o\s+)?([\w\s,.-]*?)\s*\.*\s*(?:\.\.\.)?\s*Applicants?.*?(?=Versus|v\/s|V\/s|v \/ s|V \/ s|versus)',re.IGNORECASE | re.DOTALL)
    simple_pattern = re.compile( r'(\d+)-\s*(?:Shri\.\s*)?((?:(?!M\.A\.C\.P\. No\.)[^\d,\n])+).*?Age.*?(\d+).*?Occ\s*:\s*([^\n]+)',re.IGNORECASE | re.DOTALL)
    address_pattern = re.compile(r'R[/@]t?\s*[-–]?\s*([\w\s,.()]+)(?=\.\s*|,)',re.IGNORECASE)

    addresses = address_pattern.findall(first_two_pages_text)
    detailed_applicants = detailed_pattern.findall(cleaned_text)
    simple_applicants = simple_pattern.findall(first_two_pages_text)
    applicants = detailed_applicants[:6] + simple_applicants[:6 - len(detailed_applicants)]
    applicant_data = {}
    for i, details in enumerate(applicants, start=1):
        if len(details) == 6:
            # Unpack 6 values
            num, prefix, name, age, occupation, _ = details
            applicant_data[f'Applicant {i} Number'] = num.strip() if num else " "
            applicant_data[f'Applicant {i} Name'] = f"{prefix.strip()} {name.strip()}" if prefix else name.strip()
            applicant_data[f'Applicant {i} Age'] = age.strip()
            applicant_data[f'Applicant {i} Occupation'] = occupation.strip()

        elif len(details) == 4:
            # Unpack 4 values
            num, name, age, occupation = details
            applicant_data[f'Applicant {i} Number'] = num.strip() if num else " "
            applicant_data[f'Applicant {i} Name'] = name.strip()
            applicant_data[f'Applicant {i} Age'] = age.strip()
            applicant_data[f'Applicant {i} Occupation'] = occupation.strip()

        # Assign address to each applicant
        if i - 1 < len(addresses):
            applicant_data[f'Applicant {i} Address'] = addresses[i - 1].strip()
        else:
            applicant_data[f'Applicant {i} Address'] = ""

    #print(applicant_data)
    return applicant_data


def add_applicant_columns(df, max_applicants):
    for i in range(1, max_applicants + 1):
        df[f'Applicant {i} Number'] = None
        df[f'Applicant {i} Name'] = None
        df[f'Applicant {i} Age'] = None
        df[f'Applicant {i} Occupation'] = None

def extract_opponents(cleaned_text, first_two_pages_text):
    # Existing detailed opponent pattern
    detailed_opponent_pattern = re.compile(r'(\d+)-?\s*(?:(Mr\.|Ms\.|Mrs\.|Smt\.|The Manager,|M/s)\s+)?([A-Za-z\s.]+?),?\s*Age\s*[:-]?\s*(\d+)\s*years?,?\s*Occ\.*\s*[:-]?\s*([A-Za-z\s]+),?\s*R?/?at\s*([A-Za-z0-9,\s.\/-]+)',re.IGNORECASE)
    # Updated general opponent pattern to match the provided samples
    general_opponent_pattern = re.compile(r'(?:Vs\.|V/s)\s+([A-Za-z\s.]+?)(?:\s+&\s+|\s+and\s+|\s*[/]\s*|\s*[\]\[]\s*|$)',re.IGNORECASE   )

    # Extract detailed opponents from the complete text
    detailed_opponents = detailed_opponent_pattern.findall(cleaned_text)
    # Extract general opponents from only the first two pages
    general_opponents = general_opponent_pattern.findall(first_two_pages_text)
    opponent_data = {}
    # Process detailed opponents
    for i, (num, prefix, name, age, occupation, address) in enumerate(detailed_opponents, start=1):
        opponent_data[f'Opponent {i} Number'] = num.strip()
        opponent_data[f'Opponent {i} Name'] = f"{prefix.strip()} {name.strip()}" if prefix else name.strip()
        opponent_data[f'Opponent {i} Age'] = age.strip()
        opponent_data[f'Opponent {i} Occupation'] = occupation.strip()
        opponent_data[f'Opponent {i} Address'] = address.strip()

    # Process general opponents (only from the first two pages)
    for i, opponent in enumerate(general_opponents, start=len(detailed_opponents) + 1):
        opponent = opponent.strip().rstrip(',').strip()
        opponent_data[f'Opponent {i} Name'] = opponent
    return opponent_data


def process_pdfs_in_folder(folder_path, df):
    all_files = os.listdir(folder_path)
    pdf_files = [file for file in all_files if file.lower().endswith('.pdf')]
    for pdf_file in pdf_files:
        pdf_path = os.path.join(folder_path, pdf_file)
        print(f"Processing {pdf_file}...")
        cleaned_text = extract_and_clean_text_from_pdf(pdf_path)
        doc = nlp(cleaned_text)
        doc = fitz.open(pdf_path)
        first_two_pages_text = ""
        for page_num in range(min(2, doc.page_count)):
            first_two_pages_text += doc[page_num].get_text()

        # Define patterns for each date

        received_or_presented_on_pattern = re.compile(r'(?:RECEIVED ON|Presented on)\s*:\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        #received_or_presented_on_pattern = re.compile(r'(?:RECEIVED ON|Received on|Presented on)\s*:\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        received_or_presented_on_pattern1 = re.compile(r'Received\s*on\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        registered_on_pattern = re.compile(r'Registered on\s*:\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        decided_on_pattern = re.compile(r'Decided on\s*:\s*(\d{2}[./]\d{2}[./]\d{4})', re.IGNORECASE)
        duration_pattern_multiline = re.compile(r'Duration\s*:\s*Ys/\s*Ms/\s*Ds/\s*\n\s*(\d{2})\s+(\d{2})\s+(\d{2})', re.IGNORECASE)
        duration_pattern_singleline = re.compile(r'DURATION\s*:\s*(\d+)(?:Ys|Y)[.\s]*(\d+)(?:Ms|M)[.\s]*(\d+)(?:Ds|D)[.\s]*', re.IGNORECASE)

         # Pattern to match 'DURATION : 3Ys.3Ms.2Ds.' format
        pattern_duration_uppercase = re.compile(r'DURATION\s*:\s*(\d+)(?:Ys|Y)[.\s]*(\d+)(?:Ms|M)[.\s]*(\d+)(?:Ds|D)[.\s]*', re.IGNORECASE)
        pattern_duration_colon = re.compile(r'Duration:\s*(\d+)\s*Ys[.\s]*(\d+)\s*Ms[.\s]*(\d+)\s*Ds', re.IGNORECASE)
        pattern_duration_combined = re.compile(r'(\d+)\s*Ys?[.\s]*(\d+)\s*Ms?[.\s]*(\d+)\s*Ds?|(\d+)\s*[Yy][.\s]*(\d{2})\s*[Mm][.\s]*(\d{2})\s*[Dd]s?', re.IGNORECASE)

        # Flexible pattern to match various formats, including negative values for months
        pattern_duration_flexible = re.compile(r'DURATION\s*:\s*(-?\d+)\s*(?:Ys?\.?|Y\.?)\s*(-?\d*)\s*(?:Ms?\.?|M\.?)\s*(-?\d*)\s*(?:Ds?\.?|D\.?)', re.IGNORECASE)

        # Regular expression to extract years, months, and days

        pattern_duration_flexible2 = re.compile(r'--Y\.(\d+)Ms\.(\d+)Ds\.')
        pattern_duration_flexible1 = re.compile(r'Duration\s*Ys\.\s*Ms\.\s*Ds\.\s*(\d+)\s*(\d*)\s*(\d*)', re.IGNORECASE )

        #pattern_duration_colon1 = re.compile(r'Duration: :\s*(\d+)\s*Y[.\s]*(\d{2})\s*M[.\s]*(\d{2})\s*Ds', re.IGNORECASE)

        # Search for each date

        received_on_match = received_or_presented_on_pattern.search(cleaned_text)
        received_on_match1 = received_or_presented_on_pattern1.search(cleaned_text)
        registered_on_match = registered_on_pattern.search(cleaned_text)
        decided_on_match = decided_on_pattern.search(cleaned_text)
        # Extract dates
        received_on = received_on_match.group(1) if received_on_match else received_on_match1.group(1) if received_on_match1 else " "
        registered_on = registered_on_match.group(1) if registered_on_match else " "
        decided_on = decided_on_match.group(1) if decided_on_match else " "
 
        def extract_durations(cleaned_text):
            # Check if the word "Duration:" is present in the input text
            if "Duration :" in cleaned_text:
                # Extract all numbers following "Duration:" from the input text
                numbers = [int(match) for match in re.findall(r'\b(\d+)\b', cleaned_text.split("Duration :")[1])]
                # Initialize years, months, and days
                years = numbers[0] if len(numbers) > 0 else 0
                months = numbers[1] if len(numbers) > 1 else 0
                days = numbers[2] if len(numbers) > 2 else 0
                duration = f"{years} years, {months} months, {days} days"
                return duration

            else:

                return " "


        # Extract durations

        duration_match_multiline = duration_pattern_multiline.search(cleaned_text)
        duration_match_singleline = duration_pattern_singleline.search(cleaned_text)
        match_duration_uppercase = pattern_duration_uppercase.search(cleaned_text)
        pattern_duration_colon = pattern_duration_colon.search(cleaned_text)
        match_duration_combined = pattern_duration_combined.search(cleaned_text)

        # Extract durations based on the flexible pattern
        match_duration_flexible = pattern_duration_flexible.search(cleaned_text)
        # Extract durations based on the flexible pattern
        match_duration_flexible1 = pattern_duration_flexible1.search(cleaned_text)
        # Search for the pattern in the line
        match_duration_flexible2 = pattern_duration_flexible2.search(cleaned_text)
        if duration_match_multiline:
            years, months, days = duration_match_multiline.groups()
            duration = f"{years} years, {months} months, {days} days"
        elif duration_match_singleline:
            years, months, days = duration_match_singleline.groups()
            duration = f"{years} years, {months} months, {days} days"

        elif match_duration_uppercase:
            years, months, days = match_duration_uppercase.groups()
            duration = f"{years} years, {months} months, {days} days"

        elif pattern_duration_colon:
            years, months, days = pattern_duration_colon.groups()
            duration = f"{years} years, {months} months, {days} days"
        elif match_duration_combined:
            groups = [group for group in match_duration_combined.groups() if group is not None]
            years, months, days = map(int, groups)
            duration = f"{years} years, {months} months, {days} days"

        elif match_duration_flexible:
            years, months, days = match_duration_flexible.groups()
            # Handle cases where years or days might be empty
            years = 0 if not years or years == '-' or years == '--' else int(years)
            months = 0 if not months or months == '-' else int(months)
            days = 0 if not days or  days == '-' else int(days)
            duration = f"{years} years, {months} months, {days} days"

        elif match_duration_flexible1:
            years, months, days = match_duration_flexible1.groups() 
            # Handle cases where years or days might be empty
            years = 0 if not years else int(years)
            months = 0 if not months else int(months)
            days = 0 if not days else int(days)
            duration = f"{years} years, {months} months, {days} days"
            # Check if a match is found and extract values

        elif match_duration_flexible2:
            months = int(match_duration_flexible2.group(1))
            days = int(match_duration_flexible2.group(2))
            years = 0
            duration = f"{years} years, {months} months, {days} days" 
        else:
            duration = extract_durations(cleaned_text)
            #print(duration)

        # Case Number
        case_number_pattern = re.compile(

            r'M\.?A\.?C\.?P\.?\s*No\.?\s*(\d+)(?:\/(\d+))?',

            re.IGNORECASE

        )

        case_number_match = case_number_pattern.search(cleaned_text)

        if case_number_match:

            # Construct the case number from the matched groups

            case_number = "MACP No." + case_number_match.group(1)

            if case_number_match.group(2):

                case_number += "/" + case_number_match.group(2)

        else:

            case_number = ""

        # CNR Number

        cnr_number_pattern = re.compile(

            r'(?:CNR No\.?|CNR)\s*:? MHSN\d{2}-?\s*0?\d{3,6}-\d{4}|MHPU\d{2}\D*\d{6}\D*\d{4}|MHPU\d{2}-?\d{3,6}-\d{4}',

            re.IGNORECASE
 
        )

        cnr_number_match = cnr_number_pattern.search(cleaned_text)
        if cnr_number_match:
            cnr_number = cnr_number_match.group(0).replace("CNR No. ", "").replace("CNR No", "").replace("CNR ", "").replace("\n", "").replace(" ", "")
        else:
            cnr_number = ""

        #Court Title
        court_title_pattern = re.compile(

            r'BEFORE THE (NATIONAL LOK-ADALAT, HELD AT PUNE|MEMBER, MOTOR ACCIDENT CLAIMS\s+TRIBUNAL, PUNE AT PUNE)',

            re.IGNORECASE | re.DOTALL

        )

        court_title_match = court_title_pattern.search(cleaned_text)

        if court_title_match:

            court_title = court_title_match.group(0).strip()

        else:

            court_title = ""


        # Judge Name

        judge_name_pattern = re.compile(r'Digitally signed by (.+?) Date:')

        judge_name_match = judge_name_pattern.search(cleaned_text)

        judge_name = judge_name_match.group(1).strip() if judge_name_match else ""

        old_claim_pattern = re.compile(r'Claim Application under Section\s+(\d+)\s+of the Motor Vehicles Act')

        old_claim_match = old_claim_pattern.search(cleaned_text)

        # New Claim Under Section pattern (for Legal Services Authority Act, 1987)

        new_claim_pattern = re.compile(r'Pune under Section (\d+) of the Legal Services Authority Act, 1987')

        new_claim_match = new_claim_pattern.search(cleaned_text)

        # Determine which pattern matches and use that

        if old_claim_match:

            claim_info = f"Section {old_claim_match.group(1)} of the Motor Vehicles Act"

        elif new_claim_match:

            claim_info = f"Section {new_claim_match.group(1)} of the Legal Services Authority Act, 1987"

        else:

            claim_info = ""

        # Brief Description of the Accident

        accident_description_pattern = re.compile(r'The petition in short, is as under\s*:\s*(.*?)(?=\. On)', re.DOTALL)

        accident_description_match = accident_description_pattern.search(cleaned_text)

        accident_description = accident_description_match.group(1).strip() if accident_description_match else ""

        # Date of Accident

        date_pattern = re.compile(r'which took place on (\d{2}\.\d{2}\.\d{4})')

        date_match = date_pattern.search(cleaned_text)

        accident_date = date_match.group(1).strip() if date_match else ""

        # Place of Accident

        place_pattern = re.compile(r'on\s([^\,\.]+? road in [^\,\.]+)(?:\.|\,)|in front of ([^\,\.]+), near [^\,\.]+, ([^\,\.]+)', re.IGNORECASE)
        place_match = place_pattern.search(cleaned_text)
        if place_match:
            if place_match.group(1):
                accident_place = place_match.group(1).strip()
            else:
                accident_place = place_match.group(2).strip() + ", " + place_match.group(3).strip()
        else:
            accident_place = ""

        # Death/Injury Details
        death_injury_pattern = re.compile(r'(deceased was seriously injured and succumbed to injuries|account of accidental death of [\w\s]+)', re.IGNORECASE)
        death_injury_match = death_injury_pattern.search(cleaned_text)
        death_injury_details = death_injury_match.group(0) if death_injury_match else ""

        # Registration No of vehicle 1
        registration_pattern = re.compile(r'registration No\.?\s*([A-Z]{2}-?\s?[0-9]{2}-?\s?[A-Z]*-?\s?[0-9]{4})',re.IGNORECASE)
        registration_match = registration_pattern.search(cleaned_text)
        registration_number = registration_match.group(1).strip() if registration_match else ""

        # Deceased/Victim Name
        name_pattern = re.compile(r'Deceased\s+([A-Za-z]+(?:\s+[A-Za-z]+){0,2})', re.IGNORECASE)
        deceased_names = name_pattern.findall(cleaned_text)
        if deceased_names:
            cleaned_deceased_name = deceased_names[0].strip()
        else:
            cleaned_deceased_name = ""

        # Deceased/Victim Age
        age_pattern = re.compile(r'age(?:d)?\s+(\d+)(?:\s+years(?:\s+old)?)?', re.IGNORECASE)
        age_match = age_pattern.search(cleaned_text)
        deceased_victim_age = age_match.group(1) if age_match else ""

        # Deceased/Victim Income
        income_pattern = re.compile(r'(?:earning|salary)\s+Rs\.\s*([0-9,/-]+)(?:\s+per month|\s+monthly)?', re.IGNORECASE)
        income_match = income_pattern.search(cleaned_text)
        deceased_victim_income = income_match.group(1) if income_match else ""

        # Deceased/Victim's Occupation
        occupation_pattern = re.compile(r'worked in ([\w\s]+) as ([\w\s]+)')
        occupation_match = occupation_pattern.search(cleaned_text)
        if occupation_match:
            company = occupation_match.group(1).strip()
            position = occupation_match.group(2).strip()
            deceased_victim_occupation = f"{position} at {company}"
        else:
            deceased_victim_occupation = ""

        # Account Number
        account_number_pattern = re.compile(r'Account Number\s*[-:]*\s*(\d+)', re.IGNORECASE)
        account_number_match = account_number_pattern.search(cleaned_text)
        account_number = account_number_match.group(1).strip() if account_number_match else ""
        #print(account_number)
        account_name_pattern = re.compile(r'Account Name\s*[-:]\s*([-\w\s,]+)',re.IGNORECASE)
        account_name_match = account_name_pattern.search(cleaned_text)
        account_name = account_name_match.group(1).strip() if account_name_match else ""
        #print(account_name)

        # Bank Name
        bank_name_pattern = re.compile(r'(State Bank of India),\s*(\w+)\s+Court Branch,\s*(Pune)|Name of Bank\s*[-:]\s*(.*?),\s*(.*?)\s+Court Branch,\s*(\w+)', re.IGNORECASE)
        bank_name_match = bank_name_pattern.search(cleaned_text)

        if bank_name_match:
            # Check if the first group (State Bank of India) is not None
            if bank_name_match.group(1) is not None:
                bank_name = bank_name_match.group(1).strip()
            # Check if the fifth group (Name of Bank) is not None
            elif bank_name_match.group(5) is not None:
                bank_name = bank_name_match.group(5).strip()
            else:
                bank_name = ""
        else:
            bank_name = ""

        # IFSC Code
        ifsc_code_pattern = re.compile(r'IFSC Code\s*[-:]*\s*(SBIN\d{6})',re.IGNORECASE)
        ifsc_code_match = ifsc_code_pattern.search(cleaned_text)
        ifsc_code = ifsc_code_match.group(1).strip() if ifsc_code_match else ""

        # Claim Rs.
        claim_pattern = re.compile(r'Claim Rs\.\s*([\d,/-]+)')
        claim_match = claim_pattern.search(cleaned_text)
        claim_amount = claim_match.group(1).strip() if claim_match else ""

        # Advocate for Applicants
        advocate_pattern = re.compile(r'Advocate for Applicants\s*:\s*([\w\s.]+?)(?=,\s*Shri\.|For opponent|$)',re.IGNORECASE | re.DOTALL)
        advocate_match = advocate_pattern.search(cleaned_text)
        advocate_name = advocate_match.group(1).strip() if advocate_match else ""

        # Advocate for opponent No.1
        advocate_opponent1_pattern = re.compile(r'Advocate for opponent No\.1\s*:\s*(.*?)(?=\s*Advocate for opponent No\. 2)', re.IGNORECASE | re.DOTALL)
        advocate_opponent1_match = advocate_opponent1_pattern.search(cleaned_text)
        advocate_opponent1_name = advocate_opponent1_match.group(1).strip() if advocate_opponent1_match else ""

        # Advocate for opponent No.2
        advocate_opponent2_pattern = re.compile(r'Advocate for opponent No\. 2\s*:\s*((?:Shri\.?\s+[A-Z]\.\s+[A-Z]\.\s+\w+)(?:\s*,\s*(?:Shri\.?\s+[A-Z]\.\s+[A-Z]\.\s+\w+))*)', re.IGNORECASE | re.DOTALL)
        advocate_opponent2_match = advocate_opponent2_pattern.search(cleaned_text)
        advocate_opponent2_name = advocate_opponent2_match.group(1).strip() if advocate_opponent2_match else ""

        # Name of Steno
        steno_pattern = re.compile(r'Name of Steno : (.+?) Date of order')
        steno_match = steno_pattern.search(cleaned_text)
        steno_name = steno_match.group(1).strip() if steno_match else ""

        # Order uploaded on
        order_uploaded_pattern = re.compile(r'Order uploaded on : (\d{2}\.\d{2}\.\d{4})')
        order_uploaded_match = order_uploaded_pattern.search(cleaned_text)
        order_uploaded_date = order_uploaded_match.group(1).strip() if order_uploaded_match else ""

        # Date of Order
        date_of_order_pattern = re.compile(r'Date of order : (\d{2}\.\d{2}\.\d{4})')
        date_of_order_match = date_of_order_pattern.search(cleaned_text)
        date_of_order = date_of_order_match.group(1).strip() if date_of_order_match else ""
        
        insurance_company_pattern = re.compile(r'\b(?:[A-Za-z]+\s)*(?:Insurance|Insurer|Ltd\.|Limited|Corporation|Corp\.|Company|Co\.|Group)\b',re.IGNORECASE)
        insurance_company_match = insurance_company_pattern.search(cleaned_text)
        insurance_company_name = insurance_company_match.group(0).strip() if insurance_company_match else " "
        
        medical_expenses_pattern = re.compile(r'Medical expenses Rs\.\s*([\d,/-]+)',re.IGNORECASE)
        medical_expenses_match = medical_expenses_pattern.search(cleaned_text)
        medical_expenses = medical_expenses_match.group(1).strip() if medical_expenses_match else " "

        fir_number_pattern = re.compile(r'FIR Exh\.\s*(\d+)',re.IGNORECASE)
        fir_number_match = fir_number_pattern.search(cleaned_text)
        fir_number = fir_number_match.group(1).strip() if fir_number_match else " "

        police_station_pattern = re.compile(r'Police Station,\s*([A-Za-z ]+)',re.IGNORECASE)
        police_station_match = police_station_pattern.search(cleaned_text)
        police_station_name = police_station_match.group(1).strip() if police_station_match else " "

        hospital_pattern = re.compile(r'(?:First hospital details\s+)?([A-Za-z ]+ Hospital)\s*(?:,|\b)(?:\s*Second hospital details\s+([A-Za-z ]+ Hospital))?',re.IGNORECASE)
        hospital_match = hospital_pattern.search(cleaned_text)
        first_hospital = hospital_match.group(1).strip() if hospital_match and hospital_match.group(1) else " "
        second_hospital = hospital_match.group(2).strip() if hospital_match and hospital_match.group(2) else None
        
        applicant_data = extract_applicants(cleaned_text, first_two_pages_text)
        opponent_data = extract_opponents(cleaned_text, first_two_pages_text)


        written_statement_pattern = re.compile(r'(Exh\.\s*\d+\s+(?:opponent\s*No\.?1|respondent)\s+filed\s+written\s+statement)(.*?)(?=Exh\.|\Z)',re.IGNORECASE)
        written_statement_match = written_statement_pattern.findall(cleaned_text)
        written_statement_content = " ".join([match[1].strip() for match in written_statement_match])
        
        written_statement_opponent2_pattern = re.compile(r'(Exh\.\s*\d+\s+opponent\s*No\.?2\s+filed\s+written\s+statement)(.*?)(?=Exh\.|\Z)',re.IGNORECASE | re.DOTALL)
        written_statement_opponent2_matches = written_statement_opponent2_pattern.findall(cleaned_text)
        written_statement_opponent2_content = " ".join([match[1].strip() for match in written_statement_opponent2_matches])

        judgment_date_pattern = re.compile(r'Delivered on (?:this )?(\d{1,2})(?:st|nd|rd|th)?\s+Day of (\w+)\s+(\d{4})', re.IGNORECASE)
        judgment_date_match = judgment_date_pattern.search(cleaned_text)
        if judgment_date_match:
            day, month, year = judgment_date_match.groups()
            judgment_date = f"{day} {month} {year}"
        else:
            judgment_date = ""


        marital_status_pattern = re.compile(r'Deceased\s+(?:was\s+)?(married|bachelor)', re.IGNORECASE)
        marital_status_match = marital_status_pattern.search(cleaned_text)
        if marital_status_match:
            marital_status = marital_status_match.group(1)
        else:
            marital_status = " "

        witness_no_1_pattern = re.compile(r'([A-Za-z\s.]+)\s+is\s+examined\s+as\s+witness\s+No\.?\s*1', re.IGNORECASE)
        # Search for witness No. 1 in the text
        witness_no_1_match = witness_no_1_pattern.search(cleaned_text)

        # Extract the witness number
        witness_no_1 = witness_no_1_match.group() if witness_no_1_match else ""  
        witness_no_2_pattern = re.compile(r'([A-Za-z\s.]+)\s+as\s+witness\s+No\.?\s*2', re.IGNORECASE)

        # Search for witness No. 2 in the text
        witness_no_2_match = witness_no_2_pattern.search(cleaned_text)

        # Extract the witness number
        witness_no_2 = witness_no_2_match.group() if witness_no_2_match else ""
        
        future_prospect_pattern = re.compile(r'Add[-:]?\s*(\d+)%\s*future\s*prospects?', re.IGNORECASE)

        # Search for the future prospect pattern in the text
        future_prospect_match = future_prospect_pattern.search(cleaned_text)

        # Extract the future prospect value if a match is found, otherwise set it to an empty string
        future_prospect_value = future_prospect_match.group(1).strip() if future_prospect_match else " "
        
        # Define the multiplier pattern
        multiplier_pattern = re.compile(r'Multiplier\s+(\d+)', re.IGNORECASE)

        # Search for the multiplier pattern in the text
        multiplier_matches = multiplier_pattern.findall(cleaned_text)

        # Extract the first multiplier value if matches are found, otherwise set it to an empty string
        multiplier_value = multiplier_matches[0].strip() if multiplier_matches else ""
        
        
        # Define the pattern
        custom_pattern = re.compile(r'Loss of spousal and filial consortium & Funeral Expenses & Loss of Estate Rs\.([\d,/-]+) \((.*)\)')

        # Search for the pattern in the text
        custom_matches = custom_pattern.findall(cleaned_text)

        # Extract the matched values
        custom_value = custom_matches[0][0].strip() if custom_matches else ""
        
        
        notional_income_pattern = re.compile(r'notional\s*income.*?Rs\.([\d,/-]+)', re.IGNORECASE)

        # Search for the notional income pattern in the text
        notional_income_matches = notional_income_pattern.findall(cleaned_text)

        # Extract the notional income values if matches are found, otherwise set it to an empty list
        notional_income_values = [match.strip() for match in notional_income_matches] if notional_income_matches else " "


        # Interest Rate
        interest_rate = ""
        phrases_to_check = ['interest on the total compensation', 'interest', 'amount at the rate of']
        for phrase in phrases_to_check:
            if phrase in cleaned_text:
                received_on_index = cleaned_text.find(phrase)
                if received_on_index != -1:
                    received_on_content = cleaned_text[received_on_index + len(phrase):].strip()
                    interest_rate_match = re.search(r'@ (\d+(\.\d+)?)% per annum', received_on_content)
                    if interest_rate_match:
                        interest_rate = interest_rate_match.group(1)
                        break  # Break the loop once interest rate is found

        # Create a dictionary to hold the extracted information
        info_dict = {col: "" for col in all_columns}
        info_dict = {
            "File Name": pdf_file,
            "RECEIVED ON": received_on,
            "REGISTERED ON": registered_on,
            "DECIDED ON": decided_on,
            "DURATION": duration,
            "Case Number": case_number,
            "CNR Number": cnr_number,
            "Court Title": court_title,
            "Judge Name": judge_name,
            "Claim Under Section": claim_info,
            "Brief Description of the Accident": accident_description,
            "Date of Accident": accident_date,
            "Place of Accident": accident_place,
            "Death/Injury Details": death_injury_details,
            "Registration No of vehicle 1": registration_number,
            "Deceased/Victim Name": cleaned_deceased_name,
            "Deceased/Victim Age": deceased_victim_age,
            "Deceased/Victim Income": deceased_victim_income,
            "Deceased/Victim's Occupation": deceased_victim_occupation,
            "Account Number": account_number,
            "Account_Name" : account_name,

            #"Bank Name": bank_name,

            "IFSC Code": ifsc_code,
            "Claim Rs.": claim_amount,
            "Advocate for Applicants": advocate_name,
            "Advocate for opponent No.1": advocate_opponent1_name,
            "Advocate for opponent No.2": advocate_opponent2_name,
            "Name of Steno": steno_name,
            "Order uploaded on": order_uploaded_date,
            "Date of Order": date_of_order,
            "Insurance company name":insurance_company_name,
            "Medical expenses":medical_expenses,
            "Fir number":fir_number,
            "Police station name":police_station_name,
            "First hospital name":first_hospital,
            "Second hospital name":second_hospital,
            "Written Statement by Opponent No.1":written_statement_content,
            "Written Statement by Opponent No.2":written_statement_opponent2_content,
            "Judgment Date" : judgment_date,
            "Deceased Marital Status" : marital_status,
            "Witness No 1 " : witness_no_1,
            "Witness No 2 "  : witness_no_2,
            "Future Prospect": future_prospect_value,
            "Multiplier": multiplier_value,
            "Loss of spousal and filial consortium & Funeral Expenses & Loss of Estate": custom_value,
            "Notional Income": notional_income_values,
            "Interest Rate": interest_rate
        }

        info_dict.update(applicant_data)
        info_dict.update(opponent_data)
        #print(f"eachfile{info_dict}")

        # Append the information to a list of DataFrames
        dfs = [df, pd.DataFrame([info_dict])]
        df = pd.concat(dfs, ignore_index=True)
        #print(df)
    return df

def unique_file_with_timestamp(base_path, suffix='.xlsx'):
    """Generate a unique file path with a timestamp, appending numbers if necessary."""

    timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")
    counter = 1
    new_path = f"{base_path}_{timestamp}{suffix}"
    while os.path.exists(new_path):
        new_path = f"{base_path}_{timestamp}_{counter}{suffix}"
        counter += 1
    return new_path
 
 


# Example usage
folder_path = r"D:\Criminal Damaged" # Replace with your folder path
df = pd.DataFrame(columns=all_columns)
result_df = process_pdfs_in_folder(folder_path, df)
 
 
# Find a unique filename with timestamp and save the DataFrame
base_filename = "Downloads"  # Base path for the file
unique_filename = unique_file_with_timestamp(base_filename)
result_df.to_excel(unique_filename, index=False)

 
# Print success message
print(f"File exported successfully as '{unique_filename}'")

Processing 173 2020.pdf...
1 Cri. Bail application No.173/20 Order below Exh.1 in Criminal Bail Application No.173/2020 (CNR MHPU01­006577­2020) Read application and say filed. Heard learned Advocate for the applicant Mr. P.D. Kamble and learned APP Mr. P.S. Agarwal. 2. The seized vehicle is no more necessary for the purpose of investigation. Keeping it idle will serve no purpose. Therefore, putting certain conditions, it would be proper to hand it over to the applicant, who is registered owner of the vehicle. Hence, I pass following order. O R D E R 1] Application is hereby allowed. 2] Seized vehicle i.e. Maruti Swift Dzire VDI BS­IV bearing registration No.MH42­AH­1811 be return to the applicant after executing supurtnama bond of Rs.5,00,000/­ (Five lakhs), after verifying the documents about title. 3] The applicant is directed not to change the nature of the vehicle or otherwise sale till completion of trial it and produced the same as and when necessary. Sd/­ Pune ( S. R. Navandar 

Processing 25 2019.pdf...
CNR No.MHPU01­000905­2019 1 Cri. Revn. No. 25/2019. Order Below Exh.1 in Cri Revn No. 25/2019 CNR No.MHPU01­000905­2019 1] Ld Adv for the petitioner Mr.Sharma has sought leave to withdraw the petition with leave to file appropriate proceeding due to change in circumstances and filing of chargesheet. Leave is granted. Accordingly the petition stands disposed off. Pune (S. R. Navander) Date 31/07/2019 Additional Sessions Judge, Pune 2 Cri. Revn. No.518/2016 – Jud. Certificate I affirm that the contents of PDF file Judgment are same word for word as per original Judgment. Name of Steno : Smt. Sarang Court name : Shri. S. R. Navander Addl Sessions Judge, Pune. Judgment dictated on : 31.07.2019 Judgment transcribed on : 31.07.2019 Judgment checked and signed by P. O. : 31.07.2019 Judgment uploaded on : 02.08.2019
Processing 293 2020.pdf...
1 Criminal M.A. No. 293/2020 ( CNR No.MHPU01-011786-2020 ) Shubham Shantaram Atkari V/s. State of Maharashtra Order Below Exh. 